In [1]:
from ckonlpy.tag import Twitter
import pickle
import re
import sys
from gensim.models import TfidfModel
from gensim.models import Word2Vec
from gensim.corpora import Dictionary
from pprint import pprint
from collections import Counter
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.decomposition import LatentDirichletAllocation
import mglearn
from pprint import pprint
from ckonlpy.tag import Twitter
import numpy as np
import gc
import copy
import pandas as pd

class Social_analysis():
    
    non_bmp_map = dict.fromkeys(range(0x10000, sys.maxunicode + 1), 0xfffd)

    def __init__(self):
        self.twitter = Twitter()
    
    def DB_to_table(self, DBname='intake', keyword='intake'):
        import pymssql
        import pandas.io.sql as pdsql
        import pandas as pd
        self.query = \
        """
        SELECT user_id, created_at, main_text, hashtags, comments, likes, current_url FROM instaPosting WHERE keyword = '{}'
        """.format(keyword)
        conn = pymssql.connect("intakedb.c63elkxbiwfc.us-east-2.rds.amazonaws.com:1433", "gh", "ghintake", DBname)
        df = pdsql.read_sql_query(self.query, con=conn)
        # df['main_text'] = df.main_text.apply(lambda x: x.replace('#',' ').translate(self.non_bmp_map))
        # df['created_at'] = df.created_at.apply(lambda x: x.strftime("%Y-%m-%d %H:%M:%S"))
        conn.close()
        self.raw_data = df.as_matrix()        
    
    def pickle_to_table(self, filename):
        with open(filename, 'rb') as f:
            data = pickle.load(f)
        data = data[1:]
        for idx, i in enumerate(data):
            data[idx][2] = i[2].replace('#', ' ').translate(self.non_bmp_map)
            data[idx][3] = '/'.join(i[3])
            data[idx][4] = '/'.join(i[4])
        self.raw_data = np.array(data)
  
    def hashtags_split(self, hashtags):        
        hashtags_split = []
        for i in hashtags:
            hashtags_split.append(i.split('/'))
        
        hashtags_list = []
        
        for i in hashtags_split:
            temp = []
            for j in i:
                if self.isHangul(j):
                    t_hashtags = j.translate(self.non_bmp_map)
                    temp.append(t_hashtags)
            hashtags_list.append(temp)
        self.hashtags_list = hashtags_list
        
        return hashtags_list
                    
    def add_keyword_dic(self, keyword_list, tag='Noun'):
        for i in keyword_list:
            if type(i) == tuple:
                self.twitter.add_dictionary(i[0], i[1])
            else:
                self.twitter.add_dictionary(i, tag)
        
    def morph_pos(self, text_list, exception_list = ['맛', '밥', '물', '몸']):
        
        morph_list = []
        noun_list = []
        adj_list = []
        verb_list = []
        nav_list = []
        
        for j in text_list:
            parsed = self.twitter.pos(j)
            temp = []
            n_temp = []
            adj_temp = []
            verb_temp = []
            nav_temp = []
            
            for i in parsed:
                if self.isHangul(i[0]):
                    if ((len(i[0]) > 1) or (i[0] in exception_list)):
                        temp.append(i)
                        if i[1] == 'Noun':
                            n_temp.append(i[0])
                            nav_temp.append(i[0])
                        elif i[1] == 'Verb':
                            adj_temp.append(i[0])
                            nav_temp.append(i[0])
                        elif i[1] == 'Adjective':
                            verb_temp.append(i[0])
                            nav_temp.append(i[0])
                    else:
                        print('{} 제외'.format(i[0]))
                else: print('{} 한글이 아님.'.format(i[0]))
            

            morph_list.append(temp)
            noun_list.append(n_temp)
            adj_list.append(adj_temp)
            verb_list.append(verb_temp)
            nav_list.append(nav_temp)

        return morph_list, nav_list, noun_list, adj_list, verb_list


    
    def pos_extractor(self, parsed):

        noun_list = []
        adj_list = []
        verb_list = []
        nav_list = []
        for i in parsed:            
            n_temp = []
            adj_temp = []
            verb_temp = []
            nav_temp = []
            if self.isHangul(i[0]):
                if ((len(i[0]) > 1) or (i[0] in exception_list)):
                    if i[1] == 'Noun':
                        n_temp.append(i[0])
                        nav_temp.append(i[0])
                    elif i[1] == 'Verb':
                        adj_temp.append(i[0])
                        nav_temp.append(i[0])
                    elif i[1] == 'Adjective':
                        verb_temp.append(i[0])
                        nav_temp.append(i[0])
                else:
                    print('{} 제외'.format(i[0]))
            else: print('{} 한글이 아님.'.format(i[0]))
            
            noun_list.append(n_temp)
            adj_list.append(adj_temp)
            verb_list.append(verb_temp)
            nav_list.append(nav_temp)
            
        return nav_list, noun_list, adj_list, verb_list

    
    
    def merge_list(self, tokenized_list):
        return [j for i in tokenized_list for j in i]

    
    def join_list(self, tokenized_list):
        joined_list = []
        for idx, i in enumerate(tokenized_list):
            joined_list.append(" ".join(i))
        return joined_list
 
    def split_list(self, untokenized_list):
        hashtag_splited = []
        for idx, i in enumerate(untokenized):
            hashtag_splited.append(i.split('/'))
            return hastag_splited
        
    def join_underbar(self, morph_list):

        all_list = []
        post_list=[]
        for i in morph_list:
            for j in i:
                post_list.append(j[0]+'_'+j[1])
            all_list.append([(' , ').join(post_list)])
            post_list=[] 
        all_list=np.array(all_list)
        
        return all_list

    def word_substitute(self, dataset, sublist):
        dataset = copy.deepcopy(dataset)
        sub_book = dict()
        for i in sublist:
            for j in i['sub_words']:
                sub_book[j] = i['main']
        gc.collect()
        for n, i in enumerate(dataset):
            dataset[n] = [sub_book.get(item,item) for item in i]

        del sub_book
        gc.collect()

        return dataset
    
    def word_delete(self, dataset, del_list):
        dataset = copy.deepcopy(dataset)

        for n, line in enumerate(dataset):
             dataset[n] = [i for i in line if i not in del_list]

        return dataset

    
    def isHangul(self, text):
        encText = text
        hanCount = len(re.findall(u'[\u3130-\u318F\uAC00-\uD7A3]+', encText))
        return hanCount > 0
    
    def convert_list(self, *tokenized_list):
        input_length = len(tokenized_list)
        lists = [[] for i in range(input_length)]

        for idx, li in enumerate(tokenized_list):
            for j in li:
                lists[idx].append(['/'.join(j)])

        converted_array = np.array(lists[0])
        for idx in range(input_length):
            try:
                converted_array = np.concatenate((converted_array, lists[idx + 1]), axis=1)
            except Exception as e:
                print(e,'끝')

        return converted_array

    def make_df(self, converted_array):
        columns = ['user_id', 'created_at', 'main_text', 'morph_list', 'nav_list', 'noun_list', 'adj_list', 'verb_list', 'hashtags', 'comments', 'likes', 'current_url']
        df = pd.DataFrame(np.hstack((intake.modified[:,:3], converted_array, intake.modified[:, 3:])), index=None, columns=columns)
        return df
    
    # 키워드 리스트 중 하나라도 있는 경우
    def word_check_or(self, text, keywords):
        if any(word in text for word in keywords): return True
        else: return False

    # 키워드 리스트에 있는 단어가 모두 있는 경우
    def word_check_and(self, text, keywords):
        if all(word in text for word in keywords): return True
        else: return False


    def word_check(self, method='and', keywords=[], df = None, column_name = None, filter_TF=True):
        if method == 'and':
            df['flag'] = df[column_name].apply(lambda x: self.word_check_and(x, keywords))
            return df[df.flag==filter_TF]

        if method == 'or':
            df['flag'] = df[column_name].apply(lambda x: self.word_check_or(x, keywords))
            return df[df.flag==filter_TF]


class SB_Word2Vec():    
    
    def __init__(self, morph_list):
        self.dct = Dictionary(morph_list)
        self.corpus = [self.dct.doc2bow(line) for line in morph_list]
        self.build_Word2Vec(morph_list)
    
    def make_Word2Vec(self, morph_list, size=50, window=2, min_count=10, iteration=100):
        self.em = Word2Vec(morph_list, size=size, window=window, min_count=min_count, iter=iteration)
        self.em_vocab = list(self.em.wv.vocab.keys())
        self.em_vocab_dic = {word:idx for idx, word in enumerate(self.em_vocab)}

    def make_Word2Sen_matrix(self): 
        vocab_size = len(self.em_vocab)
        self.sen_matrix = np.zeros((len(self.corpus), vocab_size))
        for idx, row in enumerate(self.sen_matrix):
            for idx2, frequency in self.corpus[idx]:
                    if self.dct[idx2] in self.em_vocab:
                        self.sen_matrix[idx][self.em_vocab_dic[self.dct[idx2]]] = frequency                
        self.sim_matrix = np.zeros((vocab_size, vocab_size))
        for idx, w1 in enumerate(self.em_vocab):
            for idx2, w2 in enumerate(self.em_vocab):
                self.sim_matrix[idx][idx2] =  self.em.wv.similarity(w1, w2)

        self.word2sen_matrix = np.dot(self.sim_matrix, np.transpose(self.sen_matrix))

        return self.word2sen_matrix

    def get_sim_sen(self, keyword, main_text, number=1):
        self.sim_sen_index = np.argsort(self.word2sen_matrix[self.em_vocab_dic[keyword]])
        self.most_sim_sen_index = np.argmax(self.word2sen_matrix[self.em_vocab_dic[keyword]])
        index_list = self.sim_sen_index.reshape((-1,)).tolist()
        index_list.reverse()
        
        for idx, i in enumerate(index_list[:number]):
            print(str(idx + 1))
            print(main_text[i])
        return index_list
    
    def build_Word2Vec(self, morph_list):
        self.make_Word2Vec(morph_list)
        self.make_Word2Sen_matrix()
        
        
class SB_LDA():

    def make_lda(self, morph_joined, ntopic=10, learning_method='batch', max_iter=25, random_state=0, n_words=20):        
        self.vect = CountVectorizer(max_features=10000, max_df=.15)
        self.X = self.vect.fit_transform(morph_joined)
        self.lda = LatentDirichletAllocation(n_components=ntopic, learning_method=learning_method, max_iter=max_iter, random_state=random_state)
        self.document_topics = self.lda.fit_transform(self.X)
        self.sorting = np.argsort(self.lda.components_, axis=1)[:, ::-1]
        self.feature_names = np.array(self.vect.get_feature_names())
        mglearn.tools.print_topics(topics=range(ntopic), feature_names=self.feature_names, sorting=self.sorting, topics_per_chunk=5, n_words=n_words)

    def related_doc(self, main_text_list, topic_index, number=10):
        category = np.argsort(self.document_topics[:, topic_index])[::-1]
        related_docs = []
        for i in category[:number]:
            print(i)
            print(main_text_list[i] + ".\n")
            related_docs.append((i, main_text_list[i]))
        return related_docs

class SB_Tfidf():    
    
    def __init__(self, list_morph_merged):
        self.list_morph_merged = list_morph_merged
        self.dct = Dictionary(self.list_morph_merged)
        self.corpus = [self.dct.doc2bow(line) for line in self.list_morph_merged]

    def get_tfidf(self):       
        self.model = TfidfModel(self.corpus)
        self.tfidf = []
        for i in self.corpus:
             self.tfidf.append(sorted(self.model[i], key = lambda x: x[1], reverse=True))
        self.tfidf_hangul = []
        for idx1, i in enumerate(self.tfidf):
            self.tfidf_hangul.append([(self.dct[j[0]], j[1]) for j in i])        
        
        return self.tfidf_hangul
    
def frequency(merged):
    word_count = Counter(merged)
    word_count2 = []
    for i in word_count:
        word_count2.append((i, word_count[i]))
    word_count2 = sorted(word_count2, key=lambda x: x[1], reverse = True)
    return word_count2

C:\Users\abys\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [2]:
intake = Social_analysis()

In [13]:
labnosh = Social_analysis()

## DB에서 불러온 데이터를 Social_analysis 인스턴스에 등록해도  되고,  그냥 그 데이터로 앞으로 진행해도 된다. 일단 튜토리얼은 pickle 데이터로 진행하기 때문에 아래 함수를 실행하면 intake.row_data 에 저장이 된다. 이 놈은 DB에 들어간 놈이 비슷하게 생긴 놈이다.

In [3]:
intake.pickle_to_table('Data/intake_list.txt')

In [14]:
labnosh.pickle_to_table('Data/labnosh_list.txt')

intake.DB_to_table("intake", "intake")

## 포함어, 제외어 설정해서 df 를 바꿀 수 있다.
## 파리미터는
## method='and', keywords=[], df = None, column_name = None, filter_TF=True
## method는 and/or 인데 and는 단어들이 전부다 포함되어야하고, or은 하나라도 있으면 된다.
## keywords 는 키워드
## df_name에는 데이터프레임
## column_name 참조할 컬럼
## True 는 만족하는 모든 것, False 그것 뺀 나머지

In [6]:
df_intake = pd.DataFrame(intake.raw_data, columns=['user_id', 'created_at', 'main_text', 'hashtags', 'comments', 'likes', 'current_url'])

df_new_intake = intake.word_check('or', ['흡기', '배기','도어락'], df_intake, 'hashtags', False)
df_new_intake = intake.word_check('or', ['intakefoods', 'dameulstudio', '_.ddo2', '__scarlett.k', '0.8l_korea'], df_new_intake, 'user_id', False)


C:\Users\abys\Anaconda3\lib\site-packages\ipykernel_launcher.py:253: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [17]:
df_labnosh = pd.DataFrame(labnosh.raw_data, columns=['user_id', 'created_at', 'main_text', 'hashtags', 'comments', 'likes', 'current_url'])
df_new_labnosh = labnosh.word_check('or', ['_jsyoung_','zzzzyo_s'], df_labnosh, 'user_id', False)

In [9]:
# df_new = labnosh.word_check('or', ['흡기', '배기','도어락'], df, 'hashtags', False)
# 랩노쉬 인스타지기, 돈받고 광고하는 애인듯
# df_new = labnosh.word_check('or', ['_jsyoung_','zzzzyo_s'], df_new, 'user_id', False)

In [63]:
a = df_new_intake.loc[df_new_intake['main_text'].str.contains('좋반')]

In [64]:
a

user_id                created_at  \
1038  2yoonplus  2018-03-18T01:51:08.000Z   

                                              main_text  \
1038  2yoonplus 아침 가볍지만 든든하게\n 인테이크  모닝죽  intake 쭉쭉 ...   

                                               hashtags  \
1038  아침/인테이크/모닝죽/intake/몽글몽글/morning/세상에서가장간편한아침/꿀고...   

                                     comments likes  \
1038  love_btskodai좋아요반사 부탁드려요 선팔해 주시면 맞팔해요!!   131   

                                            current_url   flag  
1038  https://www.instagram.com/p/Bgcl8VAB5Hb/?hl=ko...  False

In [19]:
print(len(df_new_intake), len(df_new_labnosh))

4604 7964


In [8]:
intake.modified = df_new_intake.as_matrix()

In [24]:
labnosh.modified = df_new_labnosh.as_matrix()

## 형태소 분석에 꼭 포함하고 싶은 단어를 추가한다. 기본적으로는 hashtag들을 noun으로 추가한다. 여기서 해쉬태그 중에 포함하고 싶지 않은 것을 빼는 것을 추천한다.

In [9]:
intake.hashtag_splited = intake.hashtags_split(intake.modified[:, 3])
print(np.shape(intake.hashtag_splited))
print(intake.hashtag_splited[0])

(4604,)
['아침식사', '죽', '모닝죽', '단호박', '인테이크', '맛스타그램', '먹스타그램', '식사대용', '다이어트', '두통', '좋아요반사', '맛집', '간편식', '아점', '아픔', '선팔은맞팔', '맛스타', '선팔', '맞팔', '먹스타', '음식', '푸드스타그램', '좋반']


In [21]:
labnosh.hashtag_splited = labnosh.hashtags_split(labnosh.raw_data[:, 3])
print(np.shape(labnosh.hashtag_splited))
print(labnosh.hashtag_splited[0])

(7980,)
['와이식단', '와이_받았다그램', '에잇템', '푸드바', '푸드바', '프로틴바', '푸드바', '푸드바', '에잇템', '랩노쉬', '초코바', '프로틴', '다이어트', '식단', '다이어트식단', '식단관리', '건강식', '다이어트그램', '다이어터그램', '다이어트계정', '다이어트소통', '다이어트기록']


## intake.add_dic_keyword() 함수는 1차원 list를 받는다.
## 데이터의 형태는 ['단어', '단어', '단어'] or [('단어', Tag), ('단어', Tag)]
## Tag는 'Noun', 'Verb', 'Adjective' 등이 있다.

In [35]:
intake.hashtag_merged = intake.merge_list(intake.hashtag_splited)

intake.add_keyword_dic(intake.hashtag_splited)

In [60]:
with open('custom_dictionary.txt', 'w', encoding='utf-8') as f:
    for i in intake.hashtag_merged:
        f.write(i + '\n')


In [22]:
labnosh.hashtag_merged = labnosh.merge_list(labnosh.hashtag_splited)

labnosh.add_keyword_dic(labnosh.hashtag_splited)

## 형태소 분석을 진행한다. 한글자는 제외시키는데 혹시 필요하다고 판단되는 글자는 exception_list 파라미터에 리스트로 넣어주면 된다.

In [36]:
intake.morph_list, intake.nav_list, intake.noun_list, intake.adj_list, intake.verb_list= intake.morph_pos(intake.modified[:, 2], exception_list=['맛', '밥', '물', '몸', '죽'])

lora 한글이 아님.
. 한글이 아님.
study 한글이 아님.
. 한글이 아님.
몇 제외
년 제외
째 제외
먹 제외
는 제외
엔 제외
하 제외
고 제외
도 제외
데 제외
면 제외
� 한글이 아님.
가 제외
데 제외
.. 한글이 아님.
다 제외
랑 제외
가 제외
오 제외
� 한글이 아님.
1122 한글이 아님.
_ 한글이 아님.
asm 한글이 아님.
. 한글이 아님.
고 제외
, 한글이 아님.
. 한글이 아님.
먹 제외
을 제외
수 제외
수 제외
요 제외
! 한글이 아님.
는 제외
일 제외
요 제외
. 한글이 아님.
감 제외
있 제외
게 제외
! 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
makemysugar 한글이 아님.
. 한글이 아님.
한 제외
잔 제외
� 한글이 아님.
! 한글이 아님.
~~ 한글이 아님.
먹 제외
는 제외
것 제외
가 제외
틈 제외
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
oats 한글이 아님.
oatmeal 한글이 아님.
oasis 한글이 아님.
_ 한글이 아님.
jaeyoon 한글이 아님.
짜 제외
. 한글이 아님.
로 제외
다 제외
. 한글이 아님.
이 제외
. 한글이 아님.
khjhmom 한글이 아님.
_ 한글이 아님.
을 제외
워 제외
시 제외
기 제외
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
ㅎ 제외
leeminwk 한글이 아님.
차 제외
받 제외
음 제외
. 한글이 아님.
은 제외
만 제외
한 제외
질 제외
vveun 한글이 아님.
제 제외
술 제외
안 제외
�� 한글이 아님.
_ 한글이 아님.
si 한글이 아님.
1 한글이 아님.
ver 한글이 아님.
_ 한글이 아님.
star 한글이 아님.
1 한글이 아님.
일 제외
1 한글이 아님.
식 제외
딱 제외
넘 제외
( 한글이 아님.
๑॔˃̶◡ 한글이 아님.
˂̶๑॓ 한글이 아님.
) 한글이 아님.
◞♡ 한글이 아님.
kyu 한글이 아님.
_ 한글이 아님

mongswel 한글이 아님.
_ 한글이 아님.
motze 한글이 아님.
의 제외
을 제외
합 제외
좋 제외
은 제외
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
을 제외
. 한글이 아님.
에 제외
�� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
1 한글이 아님.
등 제외
인 제외
과 제외
1 한글이 아님.
등 제외
의 제외
. 한글이 아님.
한 제외
는 제외
!. 한글이 아님.
아 제외
~ 한글이 아님.
�@intakefoods 한글이 아님.
. 한글이 아님.
. 한글이 아님.
면 제외
탈 제외
가 제외
요 제외
�� 한글이 아님.
. 한글이 아님.
서 제외
해 제외
요 제외
�� 한글이 아님.
. 한글이 아님.
게 제외
. 한글이 아님.
로 제외
도 제외
도 제외
. 한글이 아님.
@kiamotors 한글이 아님.
. 한글이 아님.
kr 한글이 아님.
. 한글이 아님.
�� 한글이 아님.
. 한글이 아님.
verticalwrite 한글이 아님.
인 제외
님 제외
... 한글이 아님.
저 제외
때 제외
도 제외
3 한글이 아님.
. 한글이 아님.
0 한글이 아님.
통 제외
이 제외
했 제외
한 제외
..? 한글이 아님.
요 제외
� 한글이 아님.
breakfast 한글이 아님.
. 한글이 아님.
jaym 한글이 아님.
2018 한글이 아님.
년 제외
28 한글이 아님.
일 제외
. 한글이 아님.
1 한글이 아님.
개 제외
. 한글이 아님.
음 제외
.... 한글이 아님.
약 제외
씹 제외
히 제외
고 제외
( 한글이 아님.
) 한글이 아님.
은 제외
던 제외
다 제외
꾸 제외
덕 제외
(?) 한글이 아님.
. 한글이 아님.
이 제외
좋 제외
고 제외
도 제외
좋 제외
다 제외
. 한글이 아님.
y 한글이 아님.
. 한글이 아님.
g 한글이 아님.
_ 한글이 아님.
hanna 한글이 아님.
에 제외
타 제외
면 제외
�� 한글이 아님.
yun 한글이 아님.
_ 한글이 아님.
mn 한글이 아님.
1991 한글이 아님.
넌 제외


d 한글이 아님.
. 한글이 아님.
myday 한글이 아님.
_ 한글이 아님.
1027 한글이 아님.
� 한글이 아님.
2018 한글이 아님.
. 한글이 아님.
06 한글이 아님.
. 한글이 아님.
23 한글이 아님.
� 한글이 아님.
: 한글이 아님.
, 한글이 아님.
, 한글이 아님.
: 한글이 아님.
꿀 제외
, 한글이 아님.
: 한글이 아님.
: 한글이 아님.
밤 제외
, 한글이 아님.
2 한글이 아님.
- 한글이 아님.
는 제외
배 제외
가 제외
서 제외
다 제외
못 제외
어 제외
욥 제외
. 한글이 아님.
이 제외
집 제외
에 제외
가 제외
놨 제외
!!!!! 한글이 아님.
!!!!! 한글이 아님.
이 제외
거 제외
인 제외
서 제외
어 제외
욥 제외
. 한글이 아님.
에 제외
옷 제외
만 제외
걸 제외
뎁 제외
�� 한글이 아님.
의 제외
힘 제외
은 제외
내 제외
욥 제외
. 한글이 아님.
- 한글이 아님.
고 제외
과 제외
하 제외
게 제외
에 제외
어 제외
욥 제외
. 한글이 아님.
까 제외
욥 제외
. 한글이 아님.
은 제외
어 제외
욥 제외
. 한글이 아님.
야 제외
게 제외
쬽 제외
? 한글이 아님.
들 제외
뛰 제외
었 제외
네 제외
욥 제외
�� 한글이 아님.
- 한글이 아님.
➡️ 한글이 아님.
못 제외
되 제외
면 제외
는 제외
뎁 제외
여 제외
욥 제외
. 한글이 아님.
youngbin 한글이 아님.
. 한글이 아님.
sim 한글이 아님.
2018 한글이 아님.
. 한글이 아님.
6 한글이 아님.
. 한글이 아님.
23 한글이 아님.
. 한글이 아님.
런 제외
x 한글이 아님.
�� 한글이 아님.
에 제외
! 한글이 아님.
를 제외
많 제외
이 제외
한 제외
(@zniyam 한글이 아님.
) 한글이 아님.
(@happysijoo 한글이 아님.
) 한글이 아님.
을 제외
는 제외
들 제외
이 제외
그 제외
을 제외
위 제외
한 제외
도 제외
좋 제외
았 제외
고 제외
도 제외
다 제외
! 한글이 아님.
� 한글이 아님.
가 제외


khu 한글이 아님.
_ 한글이 아님.
coop 한글이 아님.
들 제외
이 제외
하 제외
는 제외
를 제외
수 제외
있 제외
답 제외
니 제외
당 제외
의 제외
만 제외
서 제외
. 한글이 아님.
은 제외
도 제외
짱 제외
짱 제외
�✨ 한글이 아님.
당 제외
때 제외
도 제외
도 제외
도 제외
고 제외
요 제외
~ 한글이 아님.
� 한글이 아님.
. 한글이 아님.
corvina 한글이 아님.
330 한글이 아님.
야 제외
한 제외
을 제외
줘 제외
서 제외
어 제외
� 한글이 아님.
네 제외
덕 제외
에 제외
도 제외
서 제외
먹 제외
는 제외
이 제외
어 제외
� 한글이 아님.
전 제외
에 제외
1 한글이 아님.
지 제외
? 한글이 아님.
구 제외
� 한글이 아님.
앞 제외
� 한글이 아님.
을 제외
야 제외
� 한글이 아님.
obrightoo 한글이 아님.
뭘 제외
씹 제외
을 제외
수 제외
가 제외
..... 한글이 아님.
ㅜ 제외
lifestyle 한글이 아님.
snu 한글이 아님.
exam 한글이 아님.
eat 한글이 아님.
food 한글이 아님.
foodstagram 한글이 아님.
yum 한글이 아님.
eatclean 한글이 아님.
plantbased 한글이 아님.
vegan 한글이 아님.
chocolate 한글이 아님.
meal 한글이 아님.
チョコレート 한글이 아님.
試験 한글이 아님.
breakfast 한글이 아님.
. 한글이 아님.
jaym 한글이 아님.
2018 한글이 아님.
면 제외
19 한글이 아님.
일 제외
선 제외
식 제외
. 한글이 아님.
3 한글이 아님.
. 한글이 아님.
0 한글이 아님.
그 제외
. 한글이 아님.
말 제외
이 제외
. 한글이 아님.
첨 제외
에 제외
먹 제외
을 제외
땐 제외
만 제외
한 제외
것 제외
하 제외
게 제외
한 제외
하 제외
는 제외
? 한글이 아님.
hyunwoorimyy 한글이 아님.
인 제외
!!!!!! 한글이 아님.
ㅋ 제외
는 제외
니 제외
몫 제외
... 한글이 아님.
raksik.co

everything 한글이 아님.
_ 한글이 아님.
l 한글이 아님.
_ 한글이 아님.
ate 한글이 아님.
♥♥ 한글이 아님.
임 제외
^ 한글이 아님.
ㅇ 제외
^ 한글이 아님.
. 한글이 아님.
은 제외
( 한글이 아님.
⁎ᵕᴗᵕ⁎ 한글이 아님.
) 한글이 아님.
당 제외
... 한글이 아님.
이 제외
좋 제외
당 제외
ㅎ 제외
ㅎ 제외
고 제외
또 제외
또 제외
에 제외
덜 제외
게 제외
오 제외
ㅎ 제외
ㅎ 제외
. 한글이 아님.
. 한글이 아님.
diet 한글이 아님.
health 한글이 아님.
jjoobang 한글이 아님.
2 한글이 아님.
음 제외
! 한글이 아님.
happysijoo 한글이 아님.
- 한글이 아님.
했 제외
:) 한글이 아님.
로 제외
주 제외
❤️�� 한글이 아님.
도 제외
데 제외
6 한글이 아님.
에 제외
주 제외
셔 제외
서 제외
� 한글이 아님.
아 제외
워 제외
요 제외
! 한글이 아님.
�� 한글이 아님.
도 제외
많 제외
이 제외
, 한글이 아님.
는 제외
것 제외
도 제외
중 제외
! 한글이 아님.
✔️ 한글이 아님.
15 한글이 아님.
분 제외
인 제외
8 한글이 아님.
시 제외
15 한글이 아님.
분 제외
. 한글이 아님.
날 제외
이 제외
서 제외
. 한글이 아님.
✔️ 한글이 아님.
4 한글이 아님.
/ 한글이 아님.
6 한글이 아님.
요 제외
. 한글이 아님.
✔️ 한글이 아님.
썬 제외
, 한글이 아님.
젤 제외
, 한글이 아님.
젤 제외
요 제외
✔️ 한글이 아님.
2 한글이 아님.
차 제외
와 제외
더 제외
뛰 제외
✔️ 한글이 아님.
지 제외
하 제외
게 제외
2 한글이 아님.
번 제외
. 한글이 아님.
- 한글이 아님.
분 제외
들 제외
의 제외
요 제외
❤️ 한글이 아님.
- 한글이 아님.
d 한글이 아님.
. 한글이 아님.
myday 한글이 아님.
_ 한글이 아님.
1027 한글이 아님.
� 한글이 아님.
2018 한글이 아님.
. 한글이 아님.
06 한글이 아님.
. 한글이 아님.
14 한

...

avechong 한글이 아님.
_ 한글이 아님.
20160121 한글이 아님.
. 한글이 아님.
,, 한글이 아님.
� 한글이 아님.
! 한글이 아님.
래 제외
(?) 한글이 아님.
(?) 한글이 아님.
떴 제외
,,,,,,,, 한글이 아님.
� 한글이 아님.
! 한글이 아님.
도 제외
싶 제외
,,,,,, 한글이 아님.
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
☕️ 한글이 아님.
� 한글이 아님.
intakefoods 한글이 아님.
RedbeanSoup 한글이 아님.
� 한글이 아님.
Acme 한글이 아님.
instadaily 한글이 아님.
추 제외
운 제외
날 제외
_ 한글이 아님.
단 제외
_ 한글이 아님.
_ 한글이 아님.
웁 제외
다 제외
아 제외
� 한글이 아님.
. 한글이 아님.
_ 한글이 아님.
jini 한글이 아님.
___ 한글이 아님.
202 한글이 아님.
�� 한글이 아님.
+ 한글이 아님.
�� 한글이 아님.
로 제외
쉬 제외
고 제외
. 한글이 아님.
은 제외
두 제외
딸 제외
들 제외
의 제외
. 한글이 아님.
7 한글이 아님.
이 제외
요 제외
젤 제외
에 제외
� 한글이 아님.
. 한글이 아님.
에 제외
�� 한글이 아님.
. 한글이 아님.
낫 제외
자 제외
~ 한글이 아님.
잉 제외
. 한글이 아님.
. 한글이 아님.
onmytable 한글이 아님.
u 한글이 아님.
_ 한글이 아님.
shyun 한글이 아님.
- 한글이 아님.
먹 제외
을 제외
도 제외
먹 제외
을 제외
도 제외
딸 제외
� 한글이 아님.
- 한글이 아님.
게 제외
가 제외
니 제외
yeon 한글이 아님.
__ 한글이 아님.
bb 한글이 아님.
간 제외
라 제외
.. 한글이 아님.
... 한글이 아님.
귤 제외
. 한글이 아님.
intake 한글이 아님.
고 제외
냥 제외
도 제외
씹 제외
혀 제외
요 제외
� 한글이 아님.
* 한글이 아님.
본 제외
은 제외
을 제외
. 한글이 아님.
surelydo 한글이 아님.
적 제외
인 제외

bebe 한글이 아님.
. 한글이 아님.
je 한글이 아님.
. 한글이 아님.
taime 한글이 아님.
... 한글이 아님.
goodmorning 한글이 아님.
� 한글이 아님.
. 한글이 아님.
가 제외
됐 제외
!! 한글이 아님.
. 한글이 아님.
을 제외
. 한글이 아님.
만 제외
될 제외
듯 제외
. 한글이 아님.
이 제외
거 제외
난 제외
거 제외
또 제외
먹 제외
을 제외
거 제외
�� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
한 제외
개 제외
. 한글이 아님.
. 한글이 아님.
쌀 제외
쌀 제외
한 제외
. 한글이 아님.
까 제외
좋 제외
다 제외
- 한글이 아님.
에 제외
한 제외
!! 한글이 아님.
♡ 한글이 아님.
. 한글이 아님.
에 제외
앞 제외
둔 제외
. 한글이 아님.
또 제외
묵 제외
혀 제외
뒀 제외
던 제외
적 제외
인 제외
. 한글이 아님.
지 제외
좋 제외
아 제외
좋 제외
아 제외
. 한글이 아님.
. 한글이 아님.
한 제외
, 한글이 아님.
♡ 한글이 아님.
. 한글이 아님.
hy 한글이 아님.
_ 한글이 아님.
ming 한글이 아님.
87 한글이 아님.
뭐 제외
가 제외
걸 제외
까 제외
. 한글이 아님.
싶 제외
은 제외
들 제외
이 제외
만 제외
, 한글이 아님.
픈 제외
들 제외
도 제외
만 제외
아 제외
도 제외
못 제외
한 제외
다 제외
. 한글이 아님.
게 제외
뭐 제외
가 제외
. 한글이 아님.
쉬 제외
뛰 제외
면 제외
. 한글이 아님.
쉬 제외
어 제외
가 제외
는 제외
걸 제외
줬 제외
좋 제외
겠 제외
다 제외
:) 한글이 아님.
넘 제외
처 제외
이 제외
것 제외
저 제외
것 제외
기 제외
. 한글이 아님.
위 제외
한 제외
16 한글이 아님.
yun 한글이 아님.
_ 한글이 아님.
diet 한글이 아님.
D 한글이 아님.
+ 한글이 아님.
44 한글이 아님.
밤 제외
에 제외
서 제외
못 제외
던 제외
! 한글이 아님.
200 한글이 아님.
g 한글이 아님.
에 제외
꿀 제외
1 한글이 아

hayjooo 한글이 아님.
로 제외
고 제외
떡 제외
� 한글이 아님.
* 한글이 아님.
본 제외
피 제외
었 제외
happines 한글이 아님.
1981 한글이 아님.
다 제외
skim 한글이 아님.
0903 한글이 아님.
한 제외
끼 제외
~ 한글이 아님.
- 한글이 아님.
이 제외
도 제외
~ 한글이 아님.
- 한글이 아님.
도 제외
넘 제외
군 제외
~ 한글이 아님.
- 한글이 아님.
onthetable 한글이 아님.
onmytable 한글이 아님.
inmykitchen 한글이 아님.
breakfast 한글이 아님.
@intakefoods 한글이 아님.
jaen 한글이 아님.
_ 한글이 아님.
mom 한글이 아님.
이 제외
리 제외
게 제외
. 한글이 아님.
. 한글이 아님.
잰 제외
おかゆ 한글이 아님.
( 한글이 아님.
다 제외
〠 한글이 아님.
) 한글이 아님.
smile 한글이 아님.
. 한글이 아님.
mommy 한글이 아님.
_ 한글이 아님.
의 제외
과 제외
딱 제외
이 제외
� 한글이 아님.
. 한글이 아님.
( 한글이 아님.
이 제외
은 제외
을 제외
) 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
green 한글이 아님.
_ 한글이 아님.
maru 한글이 아님.
. 한글이 아님.
를 제외
먹 제외
. 한글이 아님.
�� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
_ 한글이 아님.
soongsoong 한글이 아님.
_ 한글이 아님.
과 제외
팩 제외
에 제외
있 제외
는 제외
서 제외
게 제외
만 제외
��� 한글이 아님.
- 한글이 아님.
요 제외
< 한글이 아님.
이 제외
은 제외
을 제외
> 한글이 아님.
instafood 한글이 아님.
foodpics 한글이 아님.
foodstagram 한글이 아님.
kidsmeal 한글이 아님.
cooking 한글이 아님.
koreanfood 한글이 아님.
snoopy 한글이 아님.
charliebrown 한글이 아님.
onthe

stadia 한글이 아님.
한 제외
의 제외
1 한글이 아님.
. 한글이 아님.
0 한글이 아님.
지 제외
나 제외
에 제외
쉽 제외
게 제외
것 제외
은 제외
라 제외
휘 제외
저 제외
어 제외
줘 제외
야 제외
kate 한글이 아님.
_ 한글이 아님.
butterfly 한글이 아님.
_ 한글이 아님.
effect 한글이 아님.
.. 한글이 아님.
..?? 한글이 아님.
��� 한글이 아님.
다 제외
.. 한글이 아님.
. 한글이 아님.
길 제외
에 제외
니 제외
.. 한글이 아님.
멀 제외
먹 제외
는 제외
점 제외
용 제외
~!! 한글이 아님.
음 제외
.. 한글이 아님.
가 제외
서 제외
.. 한글이 아님.
4 한글이 아님.
시 제외
쯤 제외
엔 제외
딱 제외
좋 제외
은 제외
. 한글이 아님.
7 한글이 아님.
시 제외
에 제외
엔 제외
양 제외
이 제외
는 제외
점 제외
. 한글이 아님.
와 제외
한 제외
가 제외
을 제외
주 제외
고 제외
.. 한글이 아님.
들 제외
이 제외
로 제외
을 제외
. 한글이 아님.
적 제외
와 제외
다 제외
. 한글이 아님.
쬐 제외
~ 한글이 아님.
끔 제외
만 제외
더 제외
하 제외
는 제외
... 한글이 아님.
ㅋ 제외
은 제외
별 제외
개 제외
에 제외
별 제외
네 제외
? 한글이 아님.
����✨ 한글이 아님.
_ 한글이 아님.
yoo 한글이 아님.
. 한글이 아님.
hana 한글이 아님.
517 한글이 아님.
. 한글이 아님.
20151021 한글이 아님.
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
는 제외
다 제외
아 제외
더 제외
을 제외
것 제외
� 한글이 아님.
다 제외
히 제외
히 제외
님 제외
들 제외
잘 제외
자 제외
요 제외
:-) 한글이 아님.
������ 한글이 아님.
. 한글이 아님.
. 한글이 아님.
diet 한글이 아님.
dietfood 한글이 아님.
DANO 한글이 아님.
_ 한글이 아님.
_ 한글이 아님.
_ 한글이 아님.
�� 한글이 아님.
jinaj

yoo 한글이 아님.
. 한글이 아님.
hana 한글이 아님.
517 한글이 아님.
. 한글이 아님.
2015709 한글이 아님.
차 제외
. 한글이 아님.
with 한글이 아님.
( 한글이 아님.
돌 제외
) 한글이 아님.
& 한글이 아님.
& 한글이 아님.
& 한글이 아님.
� 한글이 아님.
& 한글이 아님.
15 한글이 아님.
g 한글이 아님.
. 한글이 아님.
. 한글이 아님.
왔 제외
:-) 한글이 아님.
은 제외
! 한글이 아님.
저 제외
는 제외
져 제외
요 제외
� 한글이 아님.
보 제외
흑 제외
흑 제외
보 제외
♥️♥️♥️♥️♥️♥️ 한글이 아님.
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
님 제외
들 제외
용 제외
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
diet 한글이 아님.
dietfood 한글이 아님.
dieter 한글이 아님.
�� 한글이 아님.
yoo 한글이 아님.
. 한글이 아님.
hana 한글이 아님.
517 한글이 아님.
. 한글이 아님.
2015708 한글이 아님.
29 한글이 아님.
. 한글이 아님.
with 한글이 아님.
( 한글이 아님.
돌 제외
) 한글이 아님.
& 한글이 아님.
& 한글이 아님.
� 한글이 아님.
는 제외
에 제외
3 한글이 아님.
번 제외
요 제외
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
이 제외
히 제외
! 한글이 아님.
고 제외
집 제외
오 제외
면 제외
가 제외
� 한글이 아님.
이 제외
히 제외
수 제외
있 제외
을 제외
듯 제외
� 한글이 아님.
후 제외
불 제외
:-) 한글이 아님.
. 한글이 아님.
. 한글이 아님.
님 제외
들 제외
용 제외
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
diet 한글이 아님.
dietfood 한글이 아님.
dieter 한글이 아님.
�� 한글이 아님.
woorinamu 한글이 아님.
612 한글이 아님.
시 제외
찌 제외
yoo 한글이 아님.
. 한글이 아님.
hana 한글이 아님.
517 한글이 아님.
. 

In [ ]:
labnosh.morph_list, labnosh.nav_list, labnosh.noun_list, labnosh.adj_list, labnosh.verb_list= labnosh.morph_pos(labnosh.modified[:, 2], exception_list=['맛', '밥', '물', '몸', '죽'])

## 여기서 영준이가 해본 것처럼 조작해보고 싶으면 아래 과정을 거치면 된다.

In [61]:
converted_arr = intake.convert_list(intake.join_underbar(intake.morph_list), intake.nav_list, intake.noun_list, intake.adj_list, intake.verb_list)

converted_pd = intake.make_df(converted_arr)

# df_new.to_excel('result.csv', encoding='utf-8')

temp = df_new_intake.loc[df_new['main_text'].str.contains('좋반')]
temp.describe()

list index out of range 끝


ValueError: Shape of passed values is (13, 4604), indices imply (12, 4604)

## 빈도분석에는 merge된 list가 필요하다.

intake.nav_merged = intake.merge_list(intake.nav_list)

intake.nav_frequency = frequency(intake.nav_merged)

pprint(intake.nav_frequency)

In [30]:
labnosh.nav_merged = labnosh.merge_list(labnosh.nav_list)
labnosh.nav_frequency = frequency(labnosh.nav_merged)
pprint(labnosh.nav_frequency)

[('랩노쉬', 10880),
 ('다이어트', 2727),
 ('맛', 1697),
 ('미래형식사', 1628),
 ('올리브영', 1351),
 ('아침', 1304),
 ('오늘', 1073),
 ('일상', 1062),
 ('먹어', 1008),
 ('식사', 1003),
 ('다이어터', 1000),
 ('이벤트', 986),
 ('식사대용', 958),
 ('으로', 941),
 ('저녁', 936),
 ('먹고', 850),
 ('물', 848),
 ('다이어트식단', 826),
 ('너무', 819),
 ('먹스타그램', 786),
 ('점심', 772),
 ('쇼콜라', 765),
 ('플랫바', 749),
 ('운동', 732),
 ('미식당', 698),
 ('하는', 684),
 ('먹는', 663),
 ('간식', 660),
 ('요거트', 635),
 ('식단', 631),
 ('먹으', 622),
 ('쉐이크', 532),
 ('뮤즐리', 528),
 ('식단일기', 523),
 ('에잇템', 522),
 ('진짜', 521),
 ('많이', 501),
 ('밥', 498),
 ('소통', 496),
 ('다이어트그램', 492),
 ('까지', 480),
 ('시간', 465),
 ('있어', 460),
 ('한끼식사', 457),
 ('있는', 442),
 ('단백질', 433),
 ('맛이', 430),
 ('데일리', 420),
 ('한끼', 419),
 ('선물', 419),
 ('호박즙', 414),
 ('먹기', 410),
 ('먹었', 409),
 ('미숫가루', 409),
 ('우유', 407),
 ('하나', 406),
 ('그래놀라요거트', 406),
 ('리그램', 403),
 ('자색고구마', 401),
 ('맛스타그램', 400),
 ('챙겨', 398),
 ('푸드쉐이크', 383),
 ('두유', 381),
 ('같아', 376),
 ('그린씨리얼', 368),
 ('플랫', 363),
 ('오늘은', 

 ('야심작', 11),
 ('사탕수수', 11),
 ('자색고구마는', 11),
 ('영양밸런스', 11),
 ('중앙', 11),
 ('일상사진', 11),
 ('컬러', 11),
 ('랩노쉬라이프', 11),
 ('30일다이어트', 11),
 ('연주', 11),
 ('한주', 10),
 ('이동', 10),
 ('통밀빵', 10),
 ('그램', 10),
 ('차이', 10),
 ('누워', 10),
 ('챙겼', 10),
 ('생리', 10),
 ('밥상', 10),
 ('출장', 10),
 ('제로', 10),
 ('자세히', 10),
 ('운동가기전', 10),
 ('맛있어�', 10),
 ('빙수', 10),
 ('인분', 10),
 ('오자', 10),
 ('씻고', 10),
 ('프레', 10),
 ('붙어', 10),
 ('올라와', 10),
 ('같구', 10),
 ('곡물맛', 10),
 ('겠지', 10),
 ('와중', 10),
 ('우산', 10),
 ('달려', 10),
 ('쭈욱', 10),
 ('매일우유', 10),
 ('절반', 10),
 ('후루룩', 10),
 ('베이스', 10),
 ('무겁', 10),
 ('운동할', 10),
 ('고마워요', 10),
 ('차라리', 10),
 ('무언가', 10),
 ('도하', 10),
 ('체질개선', 10),
 ('다이어트점심', 10),
 ('버릴', 10),
 ('사라', 10),
 ('아직까지', 10),
 ('이럴', 10),
 ('사이트', 10),
 ('시럽', 10),
 ('한병에', 10),
 ('내가샀다그램', 10),
 ('군데', 10),
 ('쓸어', 10),
 ('대서', 10),
 ('회사원', 10),
 ('랩노쉬뮤즐리', 10),
 ('어떠', 10),
 ('기말고사', 10),
 ('방문', 10),
 ('폭식증극복', 10),
 ('국내산', 10),
 ('매운', 10),
 ('무게', 10),
 ('일주', 10),
 ('청춘', 10),


 ('잇네', 5),
 ('빵이의단호한식단', 5),
 ('고함량', 5),
 ('싶고', 5),
 ('여야', 5),
 ('소장', 5),
 ('나더', 5),
 ('풀어', 5),
 ('동작', 5),
 ('솔직후기', 5),
 ('끓여', 5),
 ('일전', 5),
 ('책상위작은밭아로니아', 5),
 ('극복', 5),
 ('느꼈', 5),
 ('비빔밥', 5),
 ('애스타그램', 5),
 ('조용히', 5),
 ('해결하기', 5),
 ('마시는한끼식사', 5),
 ('들어가기', 5),
 ('맞네', 5),
 ('근육량', 5),
 ('망설이', 5),
 ('밥먹기귀찮을때', 5),
 ('대리', 5),
 ('약한', 5),
 ('낫띵베럴', 5),
 ('맘에듬', 5),
 ('편했', 5),
 ('보답', 5),
 ('일과', 5),
 ('교회', 5),
 ('해보는', 5),
 ('나또', 5),
 ('다음에는', 5),
 ('단독으로', 5),
 ('게릴라', 5),
 ('매달', 5),
 ('숩니', 5),
 ('주식', 5),
 ('반복', 5),
 ('현미밥', 5),
 ('와플', 5),
 ('로스팅', 5),
 ('내리는', 5),
 ('비주얼', 5),
 ('나유', 5),
 ('들어가지', 5),
 ('하아', 5),
 ('알찬', 5),
 ('누리', 5),
 ('체험분', 5),
 ('이틀째', 5),
 ('격하게', 5),
 ('홀릭', 5),
 ('에잇백', 5),
 ('국산약콩', 5),
 ('빵야', 5),
 ('자전거', 5),
 ('없길', 5),
 ('넣기', 5),
 ('아끼', 5),
 ('쟁여놓기', 5),
 ('다노닭', 5),
 ('29차_뉴진', 5),
 ('밀스3', 5),
 ('세일할때', 5),
 ('얼어', 5),
 ('유제품', 5),
 ('편의점다이어트', 5),
 ('한정판', 5),
 ('배고플땐', 5),
 ('작심', 5),
 ('말로만', 5),
 ('이니스프리', 5),
 ('미주

 ('눈뜨먹', 3),
 ('땅콩샌드', 3),
 ('보내기', 3),
 ('높구', 3),
 ('클렌즈주스', 3),
 ('싸다', 3),
 ('참고하시', 3),
 ('반갑', 3),
 ('땡긴', 3),
 ('부끄러워', 3),
 ('뒷면', 3),
 ('눈금', 3),
 ('불끈', 3),
 ('드루', 3),
 ('하쟈', 3),
 ('빼박', 3),
 ('일하러', 3),
 ('이러한', 3),
 ('잇스타그램', 3),
 ('밝았', 3),
 ('프렌치', 3),
 ('점저', 3),
 ('오뎅', 3),
 ('플렛그레인', 3),
 ('데려와', 3),
 ('쫀독쫀독', 3),
 ('푸다', 3),
 ('알바중', 3),
 ('심야', 3),
 ('모자', 3),
 ('인척', 3),
 ('흔적', 3),
 ('잠재', 3),
 ('cu에', 3),
 ('펑크', 3),
 ('힘내야', 3),
 ('밤새', 3),
 ('끄읏', 3),
 ('나가시', 3),
 ('달라진', 3),
 ('깨알', 3),
 ('얻었', 3),
 ('좋아하던', 3),
 ('보느', 3),
 ('전해서', 3),
 ('다해', 3),
 ('개도', 3),
 ('썸머패키지', 3),
 ('타이', 3),
 ('율도', 3),
 ('생기는', 3),
 ('가공', 3),
 ('커뮤니티', 3),
 ('표면', 3),
 ('퍼플이의후기', 3),
 ('불닭', 3),
 ('저녁시간', 3),
 ('챌이_11', 3),
 ('달이', 3),
 ('숙제', 3),
 ('든든하다�', 3),
 ('많던', 3),
 ('다를', 3),
 ('올라오는', 3),
 ('초코맛�', 3),
 ('떼워', 3),
 ('택배아저씨', 3),
 ('떡집', 3),
 ('초보', 3),
 ('돌렸', 3),
 ('주르륵', 3),
 ('차단', 3),
 ('알로', 3),
 ('동물성단백질', 3),
 ('먹방요정', 3),
 ('기대중�', 3),
 ('퀘스트바', 3),
 ('이겠', 3

 ('닥터리브곤약젤리', 2),
 ('입맛저격', 2),
 ('뜯었', 2),
 ('병콩', 2),
 ('퍽퍽함', 2),
 ('용서', 2),
 ('데스', 2),
 ('베지', 2),
 ('그만하고', 2),
 ('써브웨이', 2),
 ('엔젤리너스', 2),
 ('출근중', 2),
 ('싸는', 2),
 ('지용', 2),
 ('꼬소한맛', 2),
 ('뿌셔뿌셔', 2),
 ('포토존', 2),
 ('오천원', 2),
 ('무보정', 2),
 ('좋아하신', 2),
 ('밍_아침', 2),
 ('선물해준', 2),
 ('사랑스럽', 2),
 ('메이드', 2),
 ('무시', 2),
 ('과일국밥', 2),
 ('국밥', 2),
 ('페키', 2),
 ('�이득', 2),
 ('달려가세', 2),
 ('언니네', 2),
 ('차마', 2),
 ('화애락진', 2),
 ('주황색', 2),
 ('오트밀크', 2),
 ('베러댄밀크', 2),
 ('건강하', 2),
 ('미니받았다그램', 2),
 ('롤케이크', 2),
 ('아하', 2),
 ('감안', 2),
 ('인상', 2),
 ('돼지고기', 2),
 ('체질식', 2),
 ('토체질', 2),
 ('말차두부케이크', 2),
 ('문도', 2),
 ('열렸', 2),
 ('이세', 2),
 ('여행준비', 2),
 ('둑흔둑흔', 2),
 ('어깨운동', 2),
 ('스텐딩', 2),
 ('비하인드', 2),
 ('레터', 2),
 ('플라이', 2),
 ('잉레', 2),
 ('단기', 2),
 ('인지도', 2),
 ('두두', 2),
 ('갈래', 2),
 ('탐정', 2),
 ('보고싶다', 2),
 ('주네', 2),
 ('완두콩', 2),
 ('스테', 2),
 ('비아', 2),
 ('히말라야', 2),
 ('초록색', 2),
 ('유어점심', 2),
 ('메밀소바', 2),
 ('셀레나문쓰챌린지', 2),
 ('여력', 2),
 ('뺏기', 2),
 ('신뢰', 2),
 ('관건', 2

...

 ('열받는다', 1),
 ('스트레스만땅', 1),
 ('어지러운', 1),
 ('잡으', 1),
 ('결과적으로는', 1),
 ('내의지가', 1),
 ('중요하다는걸', 1),
 ('소소', 1),
 ('샌디', 1),
 ('결코', 1),
 ('미처', 1),
 ('꿋꿋하', 1),
 ('무너뜨릴순없', 1),
 ('발전하는', 1),
 ('음료덕후', 1),
 ('액체질소', 1),
 ('사용하다', 1),
 ('다쳤', 1),
 ('동상', 1),
 ('손끝', 1),
 ('물집', 1),
 ('가츠샌드', 1),
 ('만촌동에이필라테스', 1),
 ('소도구필라테스', 1),
 ('대구필라테스', 1),
 ('대전승무원학원', 1),
 ('대전anc승무원학원', 1),
 ('희연쌤', 1),
 ('대흥동', 1),
 ('해보며', 1),
 ('장용', 1),
 ('셀레뷰', 1),
 ('립글로스', 1),
 ('불때', 1),
 ('생명', 1),
 ('맞추고', 1),
 ('임돠', 1),
 ('웃자', 1),
 ('존예존맛', 1),
 ('더사놔야지', 1),
 ('돈이없네', 1),
 ('월급날이언제더라', 1),
 ('돌아옵', 1),
 ('재신', 1),
 ('든든하지', 1),
 ('나니_171227', 1),
 ('베이크크리미치즈', 1),
 ('됴륵', 1),
 ('애가', 1),
 ('만원의행복', 1),
 ('생각되', 1),
 ('입속', 1),
 ('이상함', 1),
 ('별걱정', 1),
 ('딱이얌', 1),
 ('휴가중', 1),
 ('포켓치즈', 1),
 ('포켓치즈육포', 1),
 ('래야', 1),
 ('동원', 1),
 ('냉철', 1),
 ('내분', 1),
 ('아몰랑', 1),
 ('하트수세미', 1),
 ('명찰', 1),
 ('청년회', 1),
 ('성탄전야', 1),
 ('미사', 1),
 ('고시원', 1),
 ('경시생', 1),
 ('슬슬갈준비', 1),
 ('열음171226', 1),
 ('엔터키

 ('개든', 1),
 ('바예용', 1),
 ('입심', 1),
 ('심할', 1),
 ('좌절', 1),
 ('선식이나할껄', 1),
 ('미숫가루먹고싶네�', 1),
 ('담엔_주먹밥이나먹자', 1),
 ('입맛없을때용', 1),
 ('한국인은밥심�', 1),
 ('밥을챙겨먹자', 1),
 ('직대딩의삶', 1),
 ('개강이다�', 1),
 ('대딩들홧팅', 1),
 ('거르는편', 1),
 ('쬐꿈', 1),
 ('미니단호박', 1),
 ('확대', 1),
 ('착하죠', 1),
 ('취항저격', 1),
 ('식사해', 1),
 ('매일유업', 1),
 ('인터넷쇼핑', 1),
 ('세필', 1),
 ('붓은', 1),
 ('굵기', 1),
 ('엘스타그램', 1),
 ('데이리', 1),
 ('매스크', 1),
 ('미숫가룬데', 1),
 ('인하셔', 1),
 ('우주를드릴순없지만', 1),
 ('비니식단', 1),
 ('아이폰7plus', 1),
 ('내돈내고쓰는후기', 1),
 ('궁금한건못참아', 1),
 ('궁금템', 1),
 ('하루정리하기', 1),
 ('개강이코앞', 1),
 ('노력하면', 1),
 ('겟했', 1),
 ('쥬길것', 1),
 ('분노의올리브영', 1),
 ('잇겠', 1),
 ('그린위', 1),
 ('퍼터', 1),
 ('파란색', 1),
 ('건지는', 1),
 ('짜죠', 1),
 ('다이어트리뷰', 1),
 ('따라서', 1),
 ('대유', 1),
 ('인하구', 1),
 ('오또케', 1),
 ('없엌', 1),
 ('윗빅', 1),
 ('잘하게', 1),
 ('없눼', 1),
 ('맛이없다', 1),
 ('맛있는걸쪼금만먹을까', 1),
 ('하지만맛있는건', 1),
 ('입에대면멈추지못하지', 1),
 ('그것이진실', 1),
 ('어쩌란말이냐', 1),
 ('내길이아닌것', 1),
 ('구르미', 1),
 ('숨니', 1),
 ('한남대', 1),
 ('박보정요가', 1),
 ('원쟝님', 1),
 (

 ('먹기시러', 1),
 ('피맥', 1),
 ('치쏘', 1),
 ('먹을꺼얌', 1),
 ('서글픈', 1),
 ('대딩', 1),
 ('쪼이기', 1),
 ('잘하길', 1),
 ('한끼대용식사', 1),
 ('저녁을부탁해', 1),
 ('오다', 1),
 ('주웠', 1),
 ('논걸', 1),
 ('남편간식', 1),
 ('남편선물', 1),
 ('장보는아줌마', 1),
 ('오다주웠다', 1),
 ('뮤즈', 1),
 ('이쁜몸매', 1),
 ('이쁜척', 1),
 ('귀여운척', 1),
 ('뿌듯한', 1),
 ('진배', 1),
 ('쟈몽', 1),
 ('꽂혓나봄', 1),
 ('두뇌', 1),
 ('급찐타파', 1),
 ('홈메이드샌드위치', 1),
 ('투썸샌드위치', 1),
 ('월요일다이어트', 1),
 ('고구마라떼좋아한다면', 1),
 ('소독', 1),
 ('칭칭', 1),
 ('붙였', 1),
 ('실종', 1),
 ('ㅇㅈ', 1),
 ('그냥미숫가루맛', 1),
 ('믄흔드', 1),
 ('위풍', 1),
 ('복인', 1),
 ('박람회', 1),
 ('디저트페어', 1),
 ('행복한데', 1),
 ('모엘르', 1),
 ('옵스', 1),
 ('맛집스타그램', 1),
 ('병원밥', 1),
 ('입원', 1),
 ('먹으려했지만', 1),
 ('먹고또먹음', 1),
 ('글럿엌', 1),
 ('맛있어여', 1),
 ('마시썽', 1),
 ('연차', 1),
 ('아침메뉴로', 1),
 ('퇴근못하는', 1),
 ('퇴근요정', 1),
 ('낯선', 1),
 ('알람이안울려', 1),
 ('못들은걸까', 1),
 ('끓인', 1),
 ('지은', 1),
 ('다솜', 1),
 ('태종', 1),
 ('갚은', 1),
 ('아몬드맛와사비', 1),
 ('역곡', 1),
 ('역곡맛집', 1),
 ('청진동해장국', 1),
 ('살빼기그램', 1),
 ('의지부족', 1),
 ('고와', 1),
 ('한끼식사해결', 1),
 

 ('쇼콜라내스타일', 1),
 ('업무중', 1),
 ('어금니', 1),
 ('징징', 1),
 ('외출했', 1),
 ('맛도좋다는것', 1),
 ('갱일상', 1),
 ('갱리뷰', 1),
 ('방문해', 1),
 ('이례', 1),
 ('임직원들의성지', 1),
 ('어여오세염', 1),
 ('상호명변경', 1),
 ('특권', 1),
 ('부평역12번출구', 1),
 ('다시찾은카드지갑', 1),
 ('민낯', 1),
 ('드뎌먹어보넹', 1),
 ('오마이갓노쉬', 1),
 ('애슬리트', 1),
 ('루빈집업', 1),
 ('트레이닝복', 1),
 ('망하는', 1),
 ('20차유챌_말똥', 1),
 ('20차_말똥', 1),
 ('시냉이꺼', 1),
 ('반강제로', 1),
 ('준건가', 1),
 ('대신하고', 1),
 ('맛스타그램촵촵', 1),
 ('건자두', 1),
 ('로투스', 1),
 ('마카다미아', 1),
 ('캔메이크', 1),
 ('매트플로어치크', 1),
 ('데메테르', 1),
 ('퍼지네이블', 1),
 ('네이쳐리퍼블릭', 1),
 ('블러셔', 1),
 ('치크', 1),
 ('3년째', 1),
 ('사진구걸중', 1),
 ('오늘의튼튼이', 1),
 ('쉐이킹', 1),
 ('부린', 1),
 ('아해', 1),
 ('비린향', 1),
 ('와삭', 1),
 ('올인', 1),
 ('욜띠미', 1),
 ('괜츈한데', 1),
 ('울려', 1),
 ('다시랩노쉬쟁일타임', 1),
 ('선택장애', 1),
 ('비즈니스', 1),
 ('관계도', 1),
 ('후문', 1),
 ('단백질이필요해', 1),
 ('당분이많음', 1),
 ('다이어트대체식품', 1),
 ('펌프', 1),
 ('현이꼬', 1),
 ('대행수', 1),
 ('안드로메다', 1),
 ('로간', 1),
 ('포텐', 1),
 ('때우던', 1),
 ('금강산', 1),
 ('도식', 1),
 ('후경', 1),
 ('솟아라힘', 1),
 

 ('고마워이슬아', 1),
 ('학년연구실', 1),
 ('이렇게빨리옴', 1),
 ('잘먹을께요�', 1),
 ('꼭사겠어요', 1),
 ('다들한번씩은', 1),
 ('먹어보아요�', 1),
 ('글씨도이뻐', 1),
 ('일날햇', 1),
 ('첫차', 1),
 ('광명', 1),
 ('다희', 1),
 ('좋겧', 1),
 ('초콜릿덕후', 1),
 ('굶스타그램', 1),
 ('대비해', 1),
 ('마싯길', 1),
 ('보너스지름신', 1),
 ('섞기', 1),
 ('불가피할', 1),
 ('밥또', 1),
 ('빨간츄리닝', 1),
 ('동네오빠', 1),
 ('식탐강한', 1),
 ('독하지', 1),
 ('쇼콜라베이직', 1),
 ('당첨됐다네', 1),
 ('이게왔다네', 1),
 ('내한번', 1),
 ('먹어보겠음', 1),
 ('두근', 1),
 ('선정하', 1),
 ('펀패스', 1),
 ('윤지경', 1),
 ('진단', 1),
 ('건강상식빙고', 1),
 ('무료행사', 1),
 ('솔찍후기', 1),
 ('잘못한', 1),
 ('아메', 1),
 ('호수상회', 1),
 ('지하1층식품코너', 1),
 ('스캐너', 1),
 ('솟는', 1),
 ('잔득', 1),
 ('그래놀라요커트', 1),
 ('재활', 1),
 ('감행', 1),
 ('다하셨', 1),
 ('플라스틱병', 1),
 ('가인', 1),
 ('해결된', 1),
 ('팔린', 1),
 ('자색고구맛까지', 1),
 ('률류', 1),
 ('기회가되면', 1),
 ('토요반', 1),
 ('미술쌤', 1),
 ('많이먹을거니까', 1),
 ('완전초코맛', 1),
 ('잘_안섞임', 1),
 ('재오니', 1),
 ('마지막병', 1),
 ('펀패쓰', 1),
 ('FUN타스틱', 1),
 ('체성분분석', 1),
 ('건강상식BINGO', 1),
 ('한강난지공원', 1),
 ('나오세', 1),
 ('다이어트영양', 1),
 ('첫걸음', 1),
 (

## 여기서 내가 형태소분석시에 안짤리게 할 단어와 제외하고 싶은 단어, 대체하고 싶은 단어를 선택한다.
## 안짤리게 할 단어는 다시 위로 돌아가 추가한다.
## 대체하고 싶은 단어와 제외하고 싶은 단어는 아래 방법으로 처리한다. 일단 생략한다.

## 분석에서 제외할 단어를 리스트로 넣어준다. 인자로 넣어주는 값은 변하지 않으므로 넣어보고 마음에 안들면 다시 intake.nav_list 로 접근하면 삭제 전 파일로 돌아갈 수 있다.
## 진짜 후회없을 것 같을 때, intake.nav_list에 업데이트 하도록 하자.

In [ ]:
intake.nav_frequency = frequency(intake.nav_merged)

In [ ]:
intake.nav_frequency [:5]

In [ ]:
modified_nav_list = intake.word_delete(intake.nav_list, ['요거', '여러', '굳이'])
print(modified_nav_list[0])

## 이번에는 단어를 대체하는 것, 리스트 안에 딕셔너리 형식
#### [{'main': '최종적으로 대체하고 싶은 단어', 'sub_words':['대체할 단어', '대체할 단어']},
####  {'main': '최종적으로 대체하고 싶은 단어', 'sub_words':['대체할 단어', '대체할 단어']}]

In [ ]:
modified_nav_list_2 = intake.word_substitute(modified_nav_list, [{'main':'모닝죽', 'sub_words':['단호박', '단호박이', '꿀고구마']}])
print(modified_nav_list_2[0])

### 토픽모델링은 조인된 것이 필요하다.
### join_list 를 통해서 만들기

In [32]:
intake.morph_joined = intake.join_list(intake.nav_list)

In [33]:
labnosh.morph_joined = labnosh.join_list(labnosh.nav_list)

### 파라미터는 다음과 같다. 
#### self.make_lda(self, morph_joined, ntopic=10, learning_method='batch', max_iter=25, random_state=0, n_words=20)
#### ntopic과 n_words를 넣어주면 몇개의 토픽으로 나눌지, 몇개의 단어를 보여줄지를 정할 수 있다.

In [39]:
intake.LDA = SB_LDA()
intake.LDA.make_lda(intake.morph_joined, ntopic=5)

topic 0       topic 1       topic 2       topic 3       topic 4       
--------      --------      --------      --------      --------      
운동하는직장인       일상            미래식사          운동            저녁            
운동            먹스타그램         식사대용          곤약젤리          점심            
오늘            씨씨앙           파워젤부스트        헬스타그램         먹어            
독립운동          데일리           아미노리커버        야식            먹고            
다이어트그램        맛스타그램         구매            4칼로리          식단일기          
어제            이벤트           너무            식단조절          간식            
짐데이           소통            우유            맛있는곤약젤리       오늘            
건강한삶          건강            있는            견과류           다이어트그램        
꿈꾸는아해         맞팔            식사            간식            너무            
에서            홍삼            현정투어          식이조절          고구마           
매거진           좋아요           파워젤           오늘뭐먹지         식단            
아침운동          아침밥           있어            스타터키트         두유            
감량    

In [40]:
labnosh.LDA = SB_LDA()
labnosh.LDA.make_lda(labnosh.morph_joined, ntopic=5)

topic 0       topic 1       topic 2       topic 3       topic 4       
--------      --------      --------      --------      --------      
올리브영          미식당           이벤트           다이어터          너무            
일상            뮤즐리           선물            저녁            으로            
쇼콜라           올리브영          리그램           다이어트식단        먹어            
식사대용          두유            할인            플랫바           맛이            
먹스타그램         시리얼           스타일리쉬푸드       운동            먹는            
식사            후르츠팝          인스타           아침            하는            
아침            코코아팝          많이            점심            있는            
먹어            아침            건강한한끼         오늘            식사            
한끼식사          미식            간편식사          식단            있어            
자색고구마         간식            함께            식단일기          느낌            
소통            아몬드팝          하루영양          간식            요거트           
쉐이크           미식당뮤즐리        식사대용          다이어트그램        진짜            
그래놀라요거

### 그 토픽과 관련된 문서 10개를 보여준다. 두번째 인자는 토픽의 인덱스이고 세번째 인덱스는 보여줄 포스팅의 개수이다.

In [ ]:
topic0 = intake.LDA.related_doc(intake.modified[:,2], 0, 4)

In [ ]:
topic0 = labnosh.LDA.related_doc(labnosh.raw_data[:,2], 0, 4)

### 데이터 형식은 같고 할 줄 알겠지?

In [ ]:
intake.SB_word2vec = SB_Word2Vec(intake.nav_list)

In [ ]:
labnosh.SB_word2vec = SB_Word2Vec(labnosh.nav_list)

In [41]:
intake.flavor = intake.SB_word2vec.get_sim_sen('맛', intake.modified[:,2], 4)

1
ulimyu-
드디어 5개를 다 먹었당!!
-
� 밀스3.0 코코넛
-
일단 나는 밀스2.0 라이트 애용자임.
2.0라이트는 54g/202kcal + 우유 200ml/150kcal
2.0은 92g/400kcal + 우유 300ml/200kcal
3.0은 95g/400kcal + 우유 300ml/200kcal
우유랑 밀스한통먹으면 600kcal 이네..
그냥 밥먹자 � 맛난백반정식1끼 �
-
코코넛은 기존의 밀스랑 맛은 비슷한데
코코넛뿌스레기가 있어서 씹으면 달달한 맛이 남.
물론 기존에 씹던 다른 견과도 좀 씹힌다.
맛있음.
먹을만함.
배부름.
이건 추천한다.
근데 코코넛칩 싫어하는 사람은 먹지마라.
처음부터 끝까지 마시는동안 골고루 씹힌다.
기존에 밀스 먹는 사람은 사먹어도 �아깝지 않을듯.
어차피 2.0 곧 단종될거라서 3.0 사먹어야뎀. -
-
� 밀스3.0 핑크
-
모두가 예상한 딸기맛이다.
근데 뭔가 딸기 아이스크림 녹인 맛. 뭔가 2% 부족한 딸기맛.
밀스+딸기분말.
견과류 씹히는건 똑같다.
처음엔 좀 거부감이 드는데, 먹다보니 또 의외로 괜찮다.
지난 밀스2.0 핑크 에디션의 실패 이후로 노력을 한듯하다.
2.0핑크보다 나아 ㅋㅋㅋ 왜지 왜때문이지 ㅋㅋㅋ
하지만 둘다 돈주고 사먹으라면 나는 코코넛을 사먹겠다. -
-
� 밀스3.0 그린
-
이름처럼 그린답게 색상도 그린그림함.
일단 밀스처럼 견과씹히는거 똑같다.
이전의 밀스2.0 후레시그린 보다 더 그린그린함.. 치커리맛인지 쑥맛인지 왠지 풀맛이 더 많이 난다.
선식같은 느낌도 있음.
풀을 싫어한다면 거부감이 있을 수 있음.
나쁘지 않음. 먹을만함.
하지만 돈주고 사먹으라면 나는 차라리 코코넛을 먹겠어. -
-
� 밀스3.0 소이
-
딱히 할말이 없다.
콩맛나는 미숫가루인데, 두유맛이 진하게 날 줄 알았는데 그건 아니다.
기존 밀스에서 뭔가 진한맛이 빠진느낌.(물에 타먹어서 그런가) -
-
� 밀스3.0 그레인
-
맛은 기존의 밀스와 제일 흡사하다.
더하고 빼고 할말이 없다.
2
junes840

In [42]:
labnosh.flavor = labnosh.SB_word2vec.get_sim_sen('맛', labnosh.raw_data[:,2], 4)

1
u_pong_star_gram살이 빠지는 모습이 느껴진다!!!!!
랩노쉬 먹다가 이것도 사치라는 느낌을 받고
에너자임 다이어트 쉐이크로 갈아탔는데...
카페라떼 맛 시켰는데...미숫가루 맛이남...ㅋㅋㅋ
맛있음...ㅋㅋㅋ
 다이어트 미치도록걷기 운동 건강해지는기분 성수대교조깅 졸라힘듬 내관절ㅠㅠ 랩노쉬 에너자임다이어트쉐이크로갈아탐 김유퐁
2
atemshop.official-
아로니아즙을 더 맛있고 건강하게 즐기는 꿀팁�
감사합니다~( ღ'ᴗ'ღ )
.
 Regram @kkulsooni
-
 랩노쉬 에서 나온  아로니아즙
첨가물 없이 하나도 달지 않고 건강한 맛�
엄마가 포도즙인줄 아시고 드셨는데
드셔보시곤 이게 진짜배기네! 하셨어요
아침에 바로 한 포 뜯어서 요거트와 함께 먹었어요
-
 아로니아즙  책상위작은밭  건강즙  랩노쉬  labnosh  makeeatsimple  simpleandhealthyfood
3
diet_baki 받았다그램  랩노쉬플랫바
이거 뭐야...신세계다♥
.
� 영양정보
� 1개 33g 기준
칼로리 : 130kcal
탄수화물 : 14g
(당류 : 9g)
단백질 : 12g
지방 : 3.2g
나트륨 : 120mg
.
� 영양성분 Review
우선 제가 제일 먼저 보는
원재료명 및 함량을 살펴봤습니다�
제가 합성첨가물이나 합성착색료 등에 민감보스잖아요!
다른 것보다 판토텐산칼슘, 말토덱스트린, 황산망간이 보이더라구용�
식품안전정보포털을 통해서 확인한결과
판토텐산칼슘은 B5(비타민종류)고
말토덱스트린은 글리코겐 재합성을 위한 안전한 식품
황산망간도 이유식에 쓰일 정도로 법률산 안전하다고 하니
우선 만족�
.
칼로리는 1개 기준 130kcal고,
당류는 9g 이에요
당류함량이 살짝 아쉽지만�
해외 제품들에 비하면 적당한 수준이에요!
.
사실 제가 식품선택기준이 왕엄격한 편이라 그렇지
전체적으로 괜찮다고 판단됩니다�
.
� 맛 Review
맛은....정말 신세계...�
저녁이라서 리뷰를 위해
쪼끔만 맛보려고 했는데 다 먹었어요...��
.
제

In [49]:
intake.SB_word2vec.em.wv.most_similar('모닝죽', topn=50) 

[('꿀고구마', 0.6912281513214111),
 ('모닝죽단호박', 0.6616777181625366),
 ('모닝죽검은콩', 0.6612870097160339),
 ('단팥', 0.6550581455230713),
 ('검은콩', 0.6537477970123291),
 ('짜먹는죽', 0.6492149233818054),
 ('호박죽', 0.6139715313911438),
 ('검은콩죽', 0.6125727891921997),
 ('아침죽', 0.6119065284729004),
 ('단호박', 0.6085578799247742),
 ('단팥죽', 0.5922638177871704),
 ('단호박죽', 0.5889958739280701),
 ('죽', 0.5778065919876099),
 ('우유죽', 0.5577418804168701),
 ('모닝죽우유', 0.5495364665985107),
 ('꿀고구마죽', 0.5454896092414856),
 ('간편죽', 0.545372486114502),
 ('고구마죽', 0.5335783362388611),
 ('단호박이', 0.5328316688537598),
 ('인테이크모닝죽', 0.5326794385910034),
 ('아침대용식', 0.532624363899231),
 ('고구마', 0.5293775796890259),
 ('아침밥', 0.5098701119422913),
 ('오늘아침', 0.5058361887931824),
 ('단호박맛', 0.504515528678894),
 ('죽도', 0.5034728050231934),
 ('아침대용', 0.501480221748352),
 ('아침밥스타그램', 0.4995872974395752),
 ('올리브영', 0.49303531646728516),
 ('모닝죽꿀고구마', 0.4925554692745209),
 ('간편식', 0.48675763607025146),
 ('모닝죽단팥', 0.48226481676101685),
 ('저녁대용',

In [22]:
intake.SB_word2vec.em.wv.most_similar(positive=['아침', '맛'], negative=['운동'])

[('미숫가루', 0.5826406478881836),
 ('생각보다', 0.579865574836731),
 ('심지어', 0.5629949569702148),
 ('귀리', 0.5474948883056641),
 ('완전', 0.5468454957008362),
 ('아주', 0.5345592498779297),
 ('맛나', 0.5310249328613281),
 ('그냥', 0.5308135747909546),
 ('일단', 0.5180487036705017),
 ('좋아', 0.5167618989944458)]

In [43]:
pprint(intake.hashtag_merged)

['아침식사',
 '죽',
 '모닝죽',
 '단호박',
 '인테이크',
 '맛스타그램',
 '먹스타그램',
 '식사대용',
 '다이어트',
 '두통',
 '좋아요반사',
 '맛집',
 '간편식',
 '아점',
 '아픔',
 '선팔은맞팔',
 '맛스타',
 '선팔',
 '맞팔',
 '먹스타',
 '음식',
 '푸드스타그램',
 '좋반',
 '인테이크',
 '밀스라이트',
 '운동하는직장인',
 '식단인증',
 '하루시작',
 '간식타임',
 '아침스타그램',
 '간식',
 '식사대용',
 '건강스타그램',
 '건강그램',
 '선식',
 '식사',
 '아침식사',
 '아침',
 '먹스타그램',
 '맛있다그램',
 '맛스타그램',
 '텐바이텐',
 '텐텐쇼퍼',
 '텐텐쇼퍼3기',
 '인테이크',
 '귀리',
 '오트밀',
 '모닝귀리',
 '귀리우유',
 '일상',
 '인테이크',
 '모닝죽',
 '위워크',
 '육아한답시고',
 '너무먹어ㅎ',
 '인테이크',
 '모닝귀리',
 '인테이크',
 '간편식',
 '인테이크',
 '인테이크밀스',
 '미스터네이처',
 '도시락',
 '금주',
 '인테이크',
 '죽',
 '모닝죽',
 '다이어트',
 '인테이크',
 '인테이크푸드',
 '카페라떼',
 '벨벳초콜렛',
 '맛',
 '한끼',
 '식사',
 '다이어트',
 '언택트마켓',
 '샐러드자판기',
 '이색자판기',
 '먹스타그램',
 '직장인스타그램',
 '점심메뉴',
 '아침밥',
 '샐러드',
 '인테이크',
 '혼밥',
 '원더키친',
 '이벤트',
 '점심',
 '식단',
 '유지어터',
 '승미식단',
 '맛있다',
 '인테이크',
 '곤약현미밥',
 '버터치킨커리',
 '카레',
 '커리',
 '반숙',
 '치킨커리',
 '버터치킨',
 '다이어트',
 '다이어터',
 '식단관리',
 '다이어트소통',
 '먹스타그램',
 '다이어트식단',
 '홈쿡',
 '식단일기',
 '일상',
 '식단기록',
 '다이어트그램',
 '운동녀',
 '복근녀',
 '데

 '과한아침상',
 '오늘도',
 '열심히',
 '가즈아',
 '인테이크',
 '모닝귀리',
 '자꾸생각나',
 '고소한한끼',
 '스피루리나',
 '루테인',
 '챙겨',
 '먹을나이',
 'tto_목요일',
 '모닝죽',
 '바나나우유맛',
 '다이어트',
 '다이어터',
 '직장인다이어터',
 '다시어터',
 '아침식단',
 '내돈주고샀다그램',
 '인테이크',
 '모닝죽',
 '삶은계란',
 '체리',
 '땅180621',
 '땅_아침�',
 '아침식단',
 '식단기록',
 '다이어트식단',
 '잇클린',
 '인테이크',
 '밀스라이트',
 '다이어트',
 '다이어터',
 '다이어트그램',
 '일상',
 '데일리',
 '데일리룩',
 '블로그',
 '마켓',
 '셀카',
 '맞팔',
 '선팔',
 '좋아요',
 '오오티디',
 '여행',
 '카페',
 '이태원',
 '강남',
 '부산',
 '모닝',
 '모닝죽',
 '인테이크',
 '자연원',
 '소심식사',
 '인테이크',
 '귀리우유',
 '다이어트',
 '다이어트식단',
 '자연원',
 '소심식사',
 '미숫가루',
 '파우치죽',
 '인테이크',
 '귀리우유',
 '점심',
 '나눈야야매다이어터',
 '찌지만말자',
 '인테이크',
 '인테이크곤약젤리',
 '청포도',
 '사과',
 '망고',
 '복숭아',
 '곤약젤리',
 '다이어트간식',
 '먹스타그램',
 '맛스타그램',
 '건강한다이어트',
 '모닝죽',
 '출근',
 '여름준비',
 '더위시작',
 '인테이크',
 '모닝죽',
 '단호박',
 '아침',
 '에너지',
 '배고파',
 '간식',
 '건강간식',
 '간식박스',
 '사무실간식',
 '회사간식',
 '이벤트선물',
 '스내킹박스',
 '라지박스',
 '간식가득',
 '곧퇴근',
 '인테이크',
 '밀스라이트',
 '인테이크',
 '밀스라이트',
 '밀스라이트카페라떼',
 '한끼식사대용',
 '최고�',
 '부산',
 '해운대',
 '송정',
 '기장',
 '울산',
 '양산

 '인테이크',
 '모닝귀리',
 '모닝그래놀라',
 '그래놀라바',
 '아침대용',
 '식사대용',
 '인테이크',
 '밀스드링크',
 '딸기맛',
 '완전',
 '빈속엔',
 '오늘의지름',
 '인테이크',
 '모닝죽누룽지',
 '모닝죽',
 '누룽지',
 '누룽지죽',
 '사재기',
 '먹고살기위한몸부림',
 '인테이크',
 '곤약젤리',
 '복숭아',
 '사과',
 '일상',
 '데일리',
 '곤약',
 '젤리',
 '다이어트',
 '간식',
 '아침대용',
 '저칼로리',
 '맛있다',
 '추천',
 '일상스타그램',
 '데일리그램',
 '간식스타그램',
 '젤리스타그램',
 '다이어트그램',
 '아침스타그램',
 '맛있다그램',
 '소통',
 '공유',
 '추천스타그램',
 '힐링스타그램',
 '인테이크',
 '밀스라이트',
 '녹차맛',
 '대구',
 '데일리',
 '꿀모닝',
 '공휴일',
 '풀예약',
 '모닝죽',
 '아멜리아뷰티',
 '대구네일샵',
 '인테이크',
 '대구드릴케어',
 '드릴케어전문',
 '대구속눈썹펌잘하는곳',
 '대구네일',
 '대구왁싱',
 '대구속눈썹',
 '공휴일예약가능',
 '신나게달려보아요',
 '커스텀',
 '인테이크',
 '해운대',
 '런자매',
 '뛰용뛰용',
 '런스타그램',
 '자매런',
 '컴포트',
 '인테이크',
 '엘시스선스틱',
 '러너',
 '러닝',
 '셀스타그램',
 '일상',
 '한강',
 '얼스타그램',
 '자매런',
 '운동녀',
 '운동하는여자',
 '운스타그램',
 '다요트',
 '다이어트',
 '밀스그레인',
 '인테이크',
 '운스타그램',
 '헬스타그램',
 '산후운동',
 '맘스핏',
 '다이어터',
 '딸맘',
 '인테이크',
 '인테이크곤약젤리',
 '곤약젤리',
 '요구르트',
 '청포도',
 '복숭아',
 '사과',
 '망고',
 '밀스드링크딸기',
 '밀스라이트벨벳카카오',
 '밀스라이트말차라떼',
 '모닝귀리',
 '인테이크',
 '곤약젤리',
 '4칼로리',

 '청주',
 '청주헬스',
 '청주운동',
 '청주피티',
 '청주퍼스널트레이닝',
 '청주PT',
 '청주개인PT',
 '청주시내',
 '문화동',
 '성안동',
 '용담동',
 '인테이크',
 '향신료',
 '나의한끼',
 '연어구이',
 '마늘',
 '모닝죽',
 '고구마',
 '견과류',
 '완벽조화',
 '균형식',
 '건강식',
 '간편식',
 '닥터넛츠',
 '인테이크',
 '몸스터즈',
 '한끼',
 '저녁식사',
 '클리어',
 '인테이크',
 '일상',
 '소통',
 '용봉동',
 '상무지구',
 '동명동',
 '컨설팅',
 '봉선동',
 '광주',
 '서울',
 '부산',
 '불로동',
 '술스타그램',
 '일상스타그램',
 '차스타그램',
 '흔녀',
 '먹스타그램',
 '광천동',
 'k서포터즈',
 '세일즈공모전',
 '대상',
 '봄아츄르먹자',
 '인테이크',
 '모닝',
 '밀스드링크',
 '인테이크',
 '아침밥',
 '저녁',
 '두유',
 '인테이크',
 '맥반석계란',
 '다이어트',
 '식단기록',
 '다신샵',
 '두유습관',
 '인테이크',
 '그래놀라',
 '감동란',
 '건강하게먹기',
 '잇클린',
 '다믈스튜디오',
 '인테이크',
 '밀스',
 '라떼',
 '음식사진',
 '메뉴사진',
 '메뉴촬영',
 '푸드스타일링',
 '푸드스타일리스트',
 '온더테이블',
 '푸드스타그램',
 '포토그래퍼',
 '푸드포토그래퍼',
 '일상',
 '브런치',
 '먹스타그램',
 '인테이크',
 '세상에서가장간편한아침모닝죽',
 '마시는죽',
 '맛없다',
 '요즘',
 '돼지',
 '인테이크',
 '쇼핑',
 '식탐',
 '다이어트',
 '모르게쒀요',
 '자기반성',
 '독백',
 '내일부터다이어트',
 '내몸무게실화냐',
 '인생최대몸무게매번갱신',
 '각성',
 '세상모든향신료18종',
 '어버이날선물',
 '많은것',
 '받아',
 '고마워',
 '딸은',
 '최고',
 '꽃길만걷자',
 '좋은일만가득하길',
 

 '간편식',
 '대용식',
 '다이어트간편식',
 '아침식단',
 '빵이의단호한식단',
 '인테이크',
 '다이어트',
 '다이어터',
 '다이어트식단',
 '식단일기',
 '식단관리',
 '식단조절',
 '자취생다이어터',
 '일상',
 '플레이팅',
 '온더테이블',
 '일반식다이어트',
 '일반식단',
 '다이어트레시피',
 '잇클린',
 '식단',
 '감자수프',
 '모닝수프',
 '건강관리',
 '간때문이야',
 '피로야가라',
 '건강스타그램',
 '밀크씨슬',
 '홍경천',
 '인테이크',
 '인친',
 '맞팔',
 '선팔',
 '건강기능식품',
 '인테이크',
 '슈퍼푸드',
 '슈퍼바',
 '에너지',
 '뿜뿜',
 '외근',
 '영업',
 '영업사원',
 '필수템',
 '스내킹박스',
 '4월',
 '데일리',
 '건강간식',
 '꽃구경',
 '꽃놀이',
 '데이트',
 '유치원',
 '학교',
 '놀이터',
 '어디서든',
 '간편간식',
 '간식타임',
 '호박죽',
 '모닝죽단호박',
 '간식',
 '인테이크',
 '모닝죽',
 '뒤돌아서면배고파',
 '먹스타그램',
 '허기달래는중',
 '데일리',
 '일상',
 '소통',
 '새댁',
 '새댁소통',
 '맞팔',
 '인친',
 '청주',
 '대전',
 '세종',
 '점심',
 '떠먹는불가리스',
 '남양',
 '소이밀크',
 '인테이크',
 '검은콩선식',
 '웰츄럴',
 '다이어트',
 '다이어트식단',
 '다이어트그램',
 '다이어터',
 '클렌즈',
 '절식',
 '저열량',
 '저칼로리',
 '다이어트중',
 '다이어트음식',
 '다이어트푸드',
 '온더테이블',
 '관리하는여자',
 '운동하는여자',
 '홈트하는여자',
 '직장인다이어터',
 '인테이크',
 '모닝죽',
 '단호박',
 '샐러드',
 '인테이크모닝죽',
 '다이어트',
 '다이어터',
 '다이어트식단',
 '다이어트음식',
 '식단일기',
 '다이어트샐러드',
 '아임닭닭가슴살큐브',
 '아임닭',
 '미주

...

 '휴가',
 '아파',
 '부산',
 '해운대',
 '보고싶어',
 '디디써니',
 '다이어트커피',
 '천연비타민',
 '비타민구미',
 '굿모닝',
 '다이어트',
 '다이어터',
 '다이어트식단',
 '체중감량',
 '체중조절',
 '일상',
 '소통',
 '선팔하면맞팔',
 '선팔',
 '데일리',
 '맞팔',
 '잡스타그램',
 '일상스타그램',
 '밀가루끊기',
 '다이어터소통',
 '인테이크',
 '비타민',
 '변비',
 '다신샵',
 '다이어트',
 '다이어트그램',
 '다이어트식단',
 '식단조절',
 '저녁',
 '지하철',
 '인테이크',
 '모닝죽단팥',
 '에브리데이넛츠',
 '견과류',
 '네이쳐밸리',
 '오트앤베리',
 '요가',
 '비트',
 '아디다스',
 '운도녀',
 '씨씨앙',
 '인테이크',
 '비타민',
 '젤리',
 '힘내구미',
 '비타민젤리',
 '곰젤리',
 '건강',
 '다이어트식단',
 '다이어터',
 '저지방우유',
 '인테이크',
 '덥다',
 '여름',
 '다이어트',
 '다이어터',
 '싱그런',
 '다이어트',
 '다이어터',
 '다이어트일기',
 '다이어트식단',
 '식단일기',
 '식이조절',
 '아침식단',
 '지미식단',
 '씨씨앙',
 '인테이크',
 '힘내구미',
 '리코타치즈',
 '영양제',
 '홍삼구미',
 '인테이크',
 '면역력',
 '받았다그램',
 '씨씨앙',
 '다이어트식단',
 '잭스코코',
 '코코넛워터',
 '올리브영',
 '마그네슘',
 '씨씨앙',
 '인테이크',
 '힘내구미',
 '비타민',
 '젤리',
 '귤젤리',
 '비타민젤리',
 '다이어트',
 '건강',
 '다이어트식단',
 '다이어터',
 '곰',
 '신선한순간',
 'G마켓이간다',
 '신선하G',
 '디디써니',
 '인테이크',
 '다이어트영양제',
 '천연종합비타민',
 '비타민젤리',
 '다이어트',
 '다이어터',
 '다이어트식단',
 '체중감량',
 '체중조절',
 '일상',
 '소통',


 '다이어트음식',
 '식이요법',
 '홈트',
 '홈트레이닝',
 '다이어트푸드',
 '단백질섭취',
 '데일리',
 '데일리그램',
 '일상',
 '멀티비타민오렌지맛구미',
 '천이백엠',
 '인테이크',
 '리프레쉬',
 '인테이크',
 '빈스바',
 '영양바',
 '콩',
 '다이어트',
 '다이어트식단',
 '식단일기',
 '오늘의밥',
 '아침',
 '모닝',
 '회사원',
 '회사밥',
 '직장인',
 '직장인다이어트',
 '웰빙',
 '다이어트간식',
 '인테이크모닝죽단팥',
 '퀘스트바',
 'twinkle_바디챌린지_5탄',
 'twinkle_바디챌린지_5탄_식단',
 '초보다이어터_줄리아',
 '다이어트',
 '아침식단',
 '다이어트식단',
 '인테이크',
 '모닝죽',
 '다이어트계정맞팔해요',
 '소통해요',
 '모닝죽',
 '인테이크',
 '모닝죽',
 '단호박죽',
 '고구마죽',
 '간편한아침',
 '급할때간단히배채우기좋아용',
 '러끼도먹고싶다냥',
 '식사대용이지만하나로는안될듯',
 '미래식사',
 '선식',
 '건강식',
 '다이어트',
 '아몬드브리즈',
 '밀스',
 '인테이크',
 '다이어트식단',
 '인테이크',
 '모닝죽',
 '밀스',
 '인테이크',
 '온오프믹스',
 '선팔',
 '맞팔',
 '서울대',
 '스타트업',
 '창업',
 '데모데이',
 '식품',
 '음식',
 '에스쁘아',
 '노웨어시그니처립스틱',
 '인테이크',
 '입술을여성여성하게�',
 '밀스',
 '밀스오리지널',
 '미래지향적',
 '미래식품',
 '미래',
 '인테이크',
 '쉐이크',
 '곡물',
 '곡물쉐이크',
 '운동',
 '운동스타그램',
 '발아통밀빵',
 '헬로깔라',
 '인테이크비타민곰젤리',
 '헬로깔라',
 '헬로깔라',
 '아이스헬로깔라',
 'twinkle_바디챌린지_5탄_식단',
 '초보다이어터_줄리아',
 '다이어트',
 '다이어트식단',
 '저녁식단',
 '인테이크',
 '다신샵',
 '발아통밀빵',
 '헬

 '아침식사',
 '아침식사대용',
 '맛있다',
 '세상에서가장간편한아침',
 '맘스타그램',
 '일상',
 '소통',
 '맞팔',
 '인친',
 '육아스타그램',
 '육아소통',
 '아들딸맘',
 '좋아요',
 '등센서아기',
 '건강식품',
 '인테이크',
 '모닝죽',
 '다이어트',
 '아침대용',
 '점심대용',
 '먹스타그램',
 '맛스타그램',
 '냠냠',
 '인스타푸드',
 '고구마',
 '단호박',
 '단팥',
 '에코백분실사태로',
 '좌절하고있는내게',
 '구세주가나타나셨',
 '감사합니다',
 '에스쁘아',
 '노웨어시그니처',
 '인테이크',
 '레전드',
 '르스모킹',
 '1일1넛',
 '무화과캄퍄뉴',
 '옥수수페스토',
 '메이크커피',
 '수제요거트',
 '점심',
 '인테이크1일1넛',
 '인테이크',
 '수퍼드랍',
 '인테이크푸드',
 '모건블랙키친크로스',
 '메이크커피',
 '드립커피',
 '홈메이드',
 '일상',
 '온마이테이블',
 '홈쿡',
 '홈카페',
 '푸드스타그램',
 '푸드스타일링',
 '카페',
 '후식',
 '먹방',
 '데일리',
 '원두',
 '핸드드립',
 '커피',
 '원두',
 '멀티비타민',
 '쫀득쫀득',
 '맘스타그램',
 '줌스타그램',
 '비타민',
 '건강이최고',
 '영양제',
 '일상',
 '소통',
 '육아스타그램',
 '육아소통',
 '맞팔',
 '데일리',
 '리프레쉬',
 '인테이크',
 '건강',
 '럽스타그램',
 '아침',
 '공복운동',
 '슈스타운동',
 '함께가기프로젝트',
 '다이어트',
 '다이어터',
 '다이어트식단',
 '다이어트그램',
 '먹스타그램',
 '잇클린',
 '다이어트레시피',
 '일상',
 '운동',
 '헬스',
 '다노샵',
 '다노한웅녀',
 '다신',
 '씨씨앙',
 '다신샵',
 '모닝죽',
 '단호박죽',
 '용과',
 '인테이크',
 '다이어트',
 '다이어터',
 '다이어트식단',
 '다이어트그램',
 '식단일기',
 '저녁

 '인테이크',
 '닭가슴살',
 '파프리카',
 '다이어트',
 '다이어트그램',
 '식단',
 '저녁',
 '식단일기',
 '다이어트식단',
 '전자렌지에1분돌리면터져요',
 '주말',
 '일요일',
 '굿모닝',
 '아침',
 '오늘의아침',
 '간편식사',
 '인테이크',
 '모닝죽단팥',
 '모닝죽',
 '단팥죽',
 '인테이크푸즈',
 '맛있다그램',
 '간편하다그램',
 '신혼집',
 '카루셀리',
 '큐티폴',
 '신혼',
 '부부',
 '새댁',
 '주부',
 '직딩',
 '일상',
 '소통',
 '아이폰6s',
 '좋아요',
 '오그릭',
 '그릭요거트',
 '인테이크',
 '씨즈쓰리',
 '인테이크슈퍼바',
 '슈퍼푸드',
 '홀릭',
 '야무지개챙겨먹기',
 '요거트',
 '리얼그릭요거트',
 '발효식품',
 '요거트',
 '유산균',
 '그릭요거트',
 '진짜맛있음',
 '꾸덕꾸덕한맛',
 '오거트',
 '5대슈퍼푸드',
 '그릭요거트',
 '요거트',
 '그릭',
 '리얼그릭',
 '플레인',
 '유산균',
 '다이어트',
 '발효식품',
 '전주',
 '대전',
 '한국어디든',
 '점심',
 '금요일',
 '다이어트',
 '식단',
 '다이어트식단',
 '다이어트그램',
 '다이어터',
 '방학',
 '인테이크',
 '토달볶',
 '고구마',
 '홍서우테이블',
 '인테이크',
 '호박죽',
 '시리얼바',
 '인테이크',
 '1일1넛',
 '리터스포트미니',
 '오리털벙어리장갑',
 '얼티밋이어',
 '몰래가져가는남편이어폰',
 '성능좋다자랑하길래�',
 '1일1넛은인테이크푸즈에서보내주셨어요',
 '엄청감사히잘먹고있지요',
 '친정',
 '현경언니표견과타르트',
 '인테이크1일1넛',
 '히비스커스로즈힙',
 '인테이크',
 '슈퍼드랍',
 '1일1넛',
 '건강식품',
 '견과류',
 '액상차',
 '디자인레터스',
 '일상그램',
 '홈카페',
 '요거트',
 '수제요거트',
 '아침운동',
 '견과류',
 '인테이크1일1넛'

 '좋아요',
 '락식',
 '먹거리',
 '식품',
 '음식',
 '맛있는',
 '재미있은',
 '행복한먹거리',
 '인테이크',
 '과자',
 '캠핑',
 '착한과자',
 '초코',
 '초코볼',
 '스낵',
 '재규어',
 '에프',
 '타입',
 '에프타입',
 '카본',
 '사이드',
 '에어',
 '인테이크',
 '홀',
 '흑백',
 '흑',
 '백',
 '락식',
 '먹거리',
 '식품',
 '음식',
 '맛있는',
 '재미있은',
 '행복한먹거리',
 '캠핑',
 '아침',
 '인테이크',
 '후레이크',
 '콘프레이크',
 '프레이크',
 '옥수수',
 '쌀',
 '현미',
 '다이어트',
 '그래놀라',
 '현미시리얼사과',
 '아몬드',
 '락식',
 '먹거리',
 '식품',
 '음식',
 '맛있는',
 '재미있은',
 '행복한먹거리',
 '캠핑',
 '소금',
 '인테이크',
 '조미료',
 '양념',
 '다이어트',
 '인테이크',
 '선식',
 '다이어트',
 '인테리어',
 '조미료',
 '인테이크푸즈',
 '락식',
 '펀샵',
 '계피분말',
 '계피',
 '바질',
 '월계수잎',
 '로즈마리',
 '파슬리',
 '흑후추',
 '타입',
 '인테이크',
 '다이어트',
 '슈퍼푸드',
 '말린과일',
 '치아씨드',
 '아마씨드',
 '인테이크',
 '간식',
 '먹스타그램',
 '샵인테이크',
 '1인섭취',
 '1인가구',
 '맞춤',
 '간식',
 '야미',
 '인테이크',
 '1인',
 '포장',
 '군것질',
 '이벤트',
 '500원',
 '1봉지',
 '주문',
 '30일',
 '천연조미료',
 '인테이크',
 '교보문고',
 '하임',
 '시빅',
 '밴쿠버',
 '버나비',
 '인테이크',
 '튜닝',
 '인테이크',
 '셀카',
 '셀스타그램',
 '데일리',
 '강의',
 '교육',
 '오후',
 '인테이크',
 '복지']


most_similar(positive=None, negative=None, topn=10, restrict_vocab=None, indexer=None)¶

model.wv.most_similar(positive=['woman', 'king'], negative=['man'])
[('queen', 0.50882536), ...]

model.wv.most_similar_cosmul(positive=['woman', 'king'], negative=['man'])
[('queen', 0.71382287), ...]


model.wv.doesnt_match("breakfast cereal dinner lunch".split())
'cereal'

## TFIDF에는 merge 된 리스트를 넣어서 비교해주면 된다. 
## intake만 있어서 패스
## 토픽모델링 된 애들끼리 비교해보는 것도 좋을 듯.

In [23]:
tfidf = SB_Tfidf([intake.nav_merged, labnosh.nav_merged])
tfidf.get_tfidf()
tfidf_of_all = tfidf.tfidf_hangul

for i in tfidf_of_all:
    pprint(i[:10])
    print()

[('흡기', 0.25419146503600865),
 ('튜닝', 0.23128150466795636),
 ('좋은', 0.2160081977559215),
 ('파워젤부스트', 0.18764348491928534),
 ('카스타그램', 0.1800068314632679),
 ('자동차', 0.17346112850096726),
 ('아미노리커버', 0.1680063760323834),
 ('먹으면', 0.16364257405751628),
 ('단팥죽', 0.13418691072716335),
 ('머플러', 0.13091405924601301)]

[('으로', 0.4224923468565074),
 ('쇼콜라', 0.34686938659387423),
 ('미식당', 0.3169824681667258),
 ('많이', 0.22822737708004256),
 ('맛이', 0.19471780187384585),
 ('그래놀라요거트', 0.18384983153670095),
 ('자색고구마', 0.18203850314717682),
 ('푸드쉐이크', 0.17162336490741298),
 ('그린씨리얼', 0.16664221183622158),
 ('함께', 0.13856662179859727)]



## 디비로 넣어보자.

In [12]:
converted_array = intake.convert_list(intake.nav_list, intake.noun_list, intake.verb_list, intake.adj_list)

list index out of range 끝


In [ ]:
converted_array[:2, :]

In [14]:
df = intake.make_df(converted_array)

In [ ]:
df.haed

In [ ]:
len(intake.nav_list)

In [ ]:
df = pd.DataFrame(np.hstack((intake.modified[:,:3], converted_array, intake.modified[:, 3:])), index=None)
# 소정이가 전체 tag 포함된 것 join해주는 것 추가해주면
# df = pd.DataFrame(np.hstack((intake.modified[:,:3], morph_list, converted_array, intake.modified[:, 3:])), index=None, columns=[])
# 이걸로 하면 된다.

In [ ]:
df.head(10)

## 이 데이터 프레임을 넣어주면 될듯

In [1]:
labnosh = Social_analysis('labnosh.txt', 'labnosh.official')

meals = Social_analysis('meals.txt', 'intakefoods')

morningjuk = Social_analysis('morningjuk.txt', 'intakefoods')

easy_food = Social_analysis('easy_food.txt')

conven_food = Social_analysis('conven_food.txt')

keywords = [intake, labnosh, meals, morningjuk, easy_food, conven_food]

### 빈도분석

for i in keywords:
    print(len(i.main_text_list), len(i.morph_merged))

labnosh.morph_frequency = analyzer.frequency(labnosh.morph_merged)
pprint(labnosh.morph_frequency)

meals.morph_frequency = analyzer.frequency(meals.morph_merged)
pprint(meals.morph_frequency)

morningjuk.morph_frequency = analyzer.frequency(morningjuk.morph_merged)
pprint(morningjuk.morph_frequency)

easy_food.morph_frequency = analyzer.frequency(easy_food.morph_merged)
pprint(easy_food.morph_frequency)

conven_food.morph_frequency = analyzer.frequency(conven_food.morph_merged)
pprint(conven_food.morph_frequency)

### 토픽모델링

intake.LDA = analyzer.SB_LDA()
intake.LDA.make_lda(intake.morph_joined, ntopic=10)

topic0 = intake.LDA.related_doc(intake.main_text_list, 0)

topic1 = intake.LDA.related_doc(intake.main_text_list, 1)

topic2 = intake.LDA.related_doc(intake.main_text_list, 2)

topic3 = intake.LDA.related_doc(intake.main_text_list, 3)

topic7 = intake.LDA.related_doc(intake.main_text_list, 7)

topic9 = intake.LDA.related_doc(intake.main_text_list, 9)

topic3 = intake.LDA.related_doc(intake.main_text_list, 3)



labnosh.LDA = analyzer.SB_LDA()
labnosh.LDA.make_lda(labnosh.morph_joined, ntopic=10)

meals.LDA = analyzer.SB_LDA()
meals.LDA.make_lda(meals.morph_joined, ntopic=10)

morningjuk.LDA = analyzer.SB_LDA()
morningjuk.LDA.make_lda(morningjuk.morph_joined, ntopic=10)

easy_food.LDA = analyzer.SB_LDA()
easy_food.LDA.make_lda(easy_food.morph_joined, ntopic=10)

conven_food.LDA = analyzer.SB_LDA()
conven_food.LDA.make_lda(conven_food.morph_joined, ntopic=10)

### Word2Vec

intake.SB_word2vec = analyzer.SB_Word2Vec(intake.hashtags_appended)

intake.flavor = intake.SB_word2vec.get_sim_sen('맛', intake.main_hash_dic, intake.main_text_list, 4)


intake.diet = intake.SB_word2vec.get_sim_sen('다이어트', intake.main_hash_dic, intake.main_text_list, 4)


intake.health = intake.SB_word2vec.get_sim_sen('건강', intake.main_hash_dic, intake.main_text_list, 4)


intake.exercise = intake.SB_word2vec.get_sim_sen('운동', intake.main_hash_dic, intake.main_text_list, 4)


intake.morningjuk = intake.SB_word2vec.get_sim_sen('모닝죽', intake.main_hash_dic, intake.main_text_list, 4)


intake.meals = intake.SB_word2vec.get_sim_sen('밀스', intake.main_hash_dic, intake.main_text_list, 4)


intake.gonyak = intake.SB_word2vec.get_sim_sen('곤약젤리', intake.main_hash_dic, intake.main_text_list, 4)




### TFIDF

tfidf = analyzer.SB_Tfidf([intake.morph_merged, labnosh.morph_merged, meals.morph_merged, morningjuk.morph_merged, easy_food.morph_merged, conven_food.morph_merged])

tfidf_of_all = tfidf.tfidf_hangul

for i in tfidf_of_all:
    pprint(i[:10])
    print()

meals_juk_SB_Tfidf = analyzer.SB_Tfidf([meals.morph_merged, morningjuk.morph_merged])

tfidf_meals_juk = meals_juk_SB_Tfidf.tfidf_hangul

for i in tfidf_meals_juk:
    pprint(i[:10])
    print()

intake_meals_SB_Tfidf = analyzer.SB_Tfidf([intake.morph_merged, meals.morph_merged])

tfidf_intake_meals = intake_meals_SB_Tfidf.tfidf_hangul

for i in tfidf_intake_meals:
    pprint(i[:10])
    print()

intake_morningjuk_SB_Tfidf = analyzer.SB_Tfidf([intake.morph_merged, morningjuk.morph_merged])

tfidf_intake_morningjuk = intake_morningjuk_SB_Tfidf.tfidf_hangul

for i in tfidf_intake_morningjuk:
    pprint(i[:10])
    print()

meals_conven_food_SB_Tfidf = analyzer.SB_Tfidf([meals.morph_merged, conven_food.morph_merged])

tfidf_meals_conven_food = meals_conven_food_SB_Tfidf.tfidf_hangul

for i in tfidf_meals_conven_food:
    pprint(i[:10])
    print()

morningjuk_conven_food_SB_Tfidf = analyzer.SB_Tfidf([morningjuk.morph_merged, conven_food.morph_merged])

tfidf_morningjuk_conven_food = morningjuk_conven_food_SB_Tfidf.tfidf_hangul

for i in tfidf_meals_conven_food:
    pprint(i[:10])
    print()

C:\Users\abys\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [9]:
import csv
with open('morph_list.csv', 'w', encoding='utf-8') as f:
    spamwriter = csv.writer(f, delimiter=' ',
                            quotechar='|', quoting=csv.QUOTE_MINIMAL)
    for i in intake.morph_list:
        spamwriter.writerow(i)

In [16]:
def morph_pos(text_list, add_list, del_list, exception_list = ['맛', '밥', '물', '몸']):
    morph_list = []
    noun_list = []
    adj_list = []
    verb_list = []

    for j in text_list:
        parsed = self.twitter.pos(j)
        temp = []
        n_temp = []
        adj_temp = []
        verb_temp = []

        for i in parsed:
            if self.isHangul(i):
                if not i[0] in del_list:
                    if len(i[0]) > 1:
                        temp.append(i)
                        if i[1] == 'Noun':
                            n_temp.append(i[0])
                        elif i[1] == 'Verb':
                            n_adj.append(i[0])
                        elif i[1] == 'Adjective':
                            n_verb.append(i[0])

                    elif i in exception_list:
                        temp.append(i)
            else: print(i, '한글이 아닙니다.')

        morph_list.append(temp)
        noun_list.append(n_temp)
        adj_list.append(adj_temp)
        verb_list.append(verb_temp)


    nav_list = noun_list + adj_list + verb_list

    return morph_list, nav_list, noun_list, adj_list, verb_list

In [ ]:

    '''def get_from_dic(self, filename):
        self.data = handler.load_by_pickle(filename)
        self.dataset, self.dataset_dic, self.main_text_list, self.morph_list, self.morph_merged, self.morph_joined, self.hashtags_merged, self.hashtags_appended, self.main_hash_dic = handler.create_datasets_with_dic(self.data)

        # dataset, main_text_list, morph_list, morph_merged, morph_joined, hashtags_merged, hashtags_appended, main_hash_dic
    def get_data_from_list(self, filename, add_list, del_list):
        self.data = handler.load_by_pickle(filename)
        self.dataset, self.main_text_list, self.morph_list, self.morph_merged, self.morph_joined, self.hashtags_merged, self.hashtags_appended, self.main_hash_dic = handler.create_datasets_with_list(self.data[1:], add_list, del_list)'''
